In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import statsmodels.api as sm
import pmdarima as pm
import itertools
from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.tsa.stattools import adfuller, acf
from statsmodels.graphics.tsaplots  import plot_acf, plot_pacf
from sklearn.metrics import mean_squared_error, mean_absolute_error
from statsmodels.tsa.arima.model import ARIMA
from statsmodels.tsa.holtwinters import SimpleExpSmoothing
from statsmodels.tsa.api import Holt
from statsmodels.tsa.holtwinters import ExponentialSmoothing
from arch import arch_model
from prophet import Prophet

# Data Load

In [71]:
gold = pd.read_csv('./data/gold.csv', index_col=0)
silver = pd.read_csv('./data/silver.csv', index_col=0)
platinum = pd.read_csv('./data/platinum.csv', index_col=0)

In [3]:
gold.rename(columns={'Date':'ds', 'Price':'y'}, inplace =True)
silver.rename(columns={'Date':'ds', 'Price':'y'}, inplace =True)
platinum.rename(columns={'Date':'ds', 'Price':'y'}, inplace =True)


In [4]:
gold['ds'] = pd.to_datetime(gold['ds'])
silver['ds'] = pd.to_datetime(silver['ds'])
platinum['ds'] = pd.to_datetime(platinum['ds'])

# Train&Test split

In [5]:
gold_forecasting_horizon = int(gold.shape[0]*0.1) 
gold_train = gold['y'][:-gold_forecasting_horizon]
gold_test = gold['y'][-gold_forecasting_horizon:]

silver_forecasting_horizon = int(silver.shape[0]*0.1) 
silver_train = silver['y'][:-silver_forecasting_horizon]
silver_test = silver['y'][-silver_forecasting_horizon:]

platinum_forecasting_horizon = int(platinum.shape[0]*0.1) 
platinum_train = platinum['y'][:-platinum_forecasting_horizon]
platinum_test = platinum['y'][-platinum_forecasting_horizon:]

In [6]:
index = ['Gold 1 step', 'Gold 5 step', 'Gold 10 step','Silver 1 step', 'Silver 5 step', \
         'Silver 10 step', 'Platinum 1 step', 'Platinum 5 step', 'Platinum 10 step']
columns = ['Actual', 'ARIMA', 'ARIMA 2','ARIMA 3',\
           'ARIMA-GARCH', 'ARIMA-GARCH 2','ARIMA-GARCH 3',\
           'Simple Exponential Smoothing','Holt\'s Exponential Smoothing', 'Holt-Winter\'s Exponential Smoothing', \
          'Prophet', 'Prophet+ARIMA']

results = {}
results = pd.DataFrame(results, index=index, columns =columns)
results = results.drop(['Actual'], axis='columns')

# Gold (1 step)

In [7]:
#ARIMA(0,1,0)
arima_errors = []
arima_preds1 = []
#ARIMA(0,1,0)-GARCH(1,1)
arch_errors = []
arch_preds1 = []
order = (0,1,0)


for i in range(gold_forecasting_horizon) :
    arima_model = ARIMA(gold['y'][:gold.shape[0]-gold_forecasting_horizon+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=1).to_numpy().item()
    arima_error = arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds1.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=1).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=1)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds1.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA'].iloc[0] = arima
results['ARIMA-GARCH'].iloc[0] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39261.71615810042
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7660.258552028359
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4653.943969686757
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6239.037255622879
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4641.627309112651
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4639.50799747101
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4639.3128749822445
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4639.028053322476
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4638.735201859315
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4638.570020008029
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4638.548815026712
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4638.548731630506
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4638.548729678076
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4638.54872

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39414.19665960208
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7680.7034801232
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4664.546124613158
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6263.831010007256
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4652.3668801450585
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4650.089408123231
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4649.9061366513615
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4649.625487195113
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4649.352390205151
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4649.2035771157625
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4649.186553133297
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4649.186492095692
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4649.186490646749
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4649.1864

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39664.859445421534
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7699.805891336317
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4674.814170068868
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6308.747740170553
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4662.833127748046
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4660.457482823625
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4660.274575246219
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4659.997594948617
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4659.72943573192
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4659.5865854411895
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4659.5705350831095
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4659.570479019221
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4659.570477801647
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4659.570

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      9,   Func. Count:     53,   Neg. LLF: 5159.571596232442
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5159.56810162263
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5159.568049901782
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5159.5680499019645
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5159.568049901782
            Iterations: 12
            Function evaluations: 67
            Gradient evaluations: 12
Iteration:      1,   Func. Count:      6,   Neg. LLF: 44057.607113455306
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8484.14535528461
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5177.990191884628
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5460.42242304876
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5163.584452059811
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5163.534401024815
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5163.47346896335
I

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 44170.96188472459
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8496.675578755792
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5184.964045226403
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5485.727685144522
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5170.513648914364
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5170.466123233661
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5170.408628227726
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5170.299987012796
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5170.273171697418
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5170.269834562792
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5170.26978440152
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5170.269784401711
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5170.26978440152
            Iterations: 12
   

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

In [8]:
#ARIMA(2,1,2)
arima_errors = []
arima_preds2_1 = []
#ARIMA(2,1,2)-GARCH(1,1)
arch_errors = []
arch_preds2_1 = []
order = (2,1,2)


for i in range(gold_forecasting_horizon) :
    arima_model = ARIMA(gold['y'][:gold.shape[0]-gold_forecasting_horizon+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=1).to_numpy().item()
    arima_error = arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds2_1.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=1).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=1)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds2_1.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 2'].iloc[0] = arima
results['ARIMA-GARCH 2'].iloc[0] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39244.27441026566
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7661.426815062393
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4653.696462362957
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6067.952211434291
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4640.6650898577045
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4638.494885401917
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4638.330611719741
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4637.919783121239
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4637.693540729209
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4637.594527948349
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4637.593227289861
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4637.593221562226
Iteration:     13,   Func. Count:     71,   Neg. LLF: 4637.5932215621615
Optimization terminated successfully    (Exit mode 0)
        

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 39434.53967356794
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7668.797919448836
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4657.513618029867
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6068.398583958461
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4644.406267079799
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4642.255849088005
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4642.094487530108
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4641.692914025088
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4641.469801003661
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4641.371886721736
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4641.370480578285
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4641.370476287567
Iteration:     13,   Func. Count:     71,   Neg. LLF: 4641.3704762874795
Optimization terminated successfully    (Exit mode 0)
         

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 39390.49899671493
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7675.267380871401
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4660.893959906792
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6073.3343229345155
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4647.86925910064
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4645.598698037378
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4645.442179206456
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4645.031521347058
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4644.823774117673
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4644.739025377412
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4644.738301505036
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4644.738298791082
Iteration:     13,   Func. Count:     71,   Neg. LLF: 4644.738298791055
Optimization terminated successfully    (Exit mode 0)
          

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood o

Iteration:      1,   Func. Count:      6,   Neg. LLF: 44126.10947467991
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8498.321831770663
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5185.895961737217
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5329.803483719944
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5170.888346266302
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5170.84657129216
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5170.773626213134
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5170.673934506582
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5170.6431354905435
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5170.639678978656
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5170.639592524519
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5170.63959252462
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5170.639592524519
            Iterations: 12
  

C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting 

Iteration:      1,   Func. Count:      6,   Neg. LLF: 44195.470677275
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8504.671446489448
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5189.926767194311
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5321.942949085629
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5174.88538994546
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5174.844918440673
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5174.77274933497
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5174.6759297060635
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5174.645898235344
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5174.642530417952
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5174.642446115933
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5174.642446116031
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5174.642446115933
            Iterations: 12
    

C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [9]:
#ARIMA(1,1,0)
arima_errors = []
arima_preds3_1 = []
#ARIMA(1,1,0)-GARCH(1,1)
arch_errors = []
arch_preds3_1 = []
order = (1,1,0)


for i in range(gold_forecasting_horizon) :
    arima_model = ARIMA(gold['y'][:gold.shape[0]-gold_forecasting_horizon+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=1).to_numpy().item()
    arima_error = arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds3_1.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=1).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=1)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds3_1.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 3'].iloc[0] = arima
results['ARIMA-GARCH 3'].iloc[0] = arch

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 39353.15924257478
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7659.8894499003745
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4653.284001395845
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6227.265031777996
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4640.93186347182
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4638.713268781978
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4638.521235161062
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4638.188924285129
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4637.906886668799
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4637.755842525962
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4637.743592793473
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4637.743543564586
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4637.7435423042625
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4637.7435

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39467.59040829539
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7680.3594632286195
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4663.9078636021795
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6253.044463324945
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4651.698865992246
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4649.320064125835
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4649.138994425857
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4648.811653141747
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4648.549447200568
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4648.415129140452
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4648.405759945888
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4648.405728552723
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4648.405727743107
Optimization terminated successfully    (Exit mode 0)
        

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 44004.12123877214
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8483.927756677347
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5177.588065033644
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5476.181326998185
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5163.173791120197
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5163.123042412767
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5163.061116681754
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5162.945147476406
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5162.916923488092
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5162.913516056541
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5162.913465142723
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5162.913465142866
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5162.913465142723
            Iterations: 12
 

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:     11,   Func. Count:     63,   Neg. LLF: 5169.851014451193
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5169.851014451371
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5169.851014451193
            Iterations: 12
            Function evaluations: 67
            Gradient evaluations: 12
Iteration:      1,   Func. Count:      6,   Neg. LLF: 44256.38610626805
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8502.584811929039
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5187.985578771708
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5517.2370433139495
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5173.543584223678
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5173.496063937506
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5173.439403579244
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5173.3319287137565
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5173.3060665737

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

In [10]:
#SES
ses_errors = []
ses_preds1 = []
#Holt
holt_errors = []
holt_preds1 = []
#Holt-Winter
hw_errors = []
hw_preds1 = []

for i in range(gold_forecasting_horizon) :
    ses_model = SimpleExpSmoothing(gold['y'][:-gold_forecasting_horizon+i])
    ses_model_fit = ses_model.fit()
    ses_pred = ses_model_fit.forecast(1).to_numpy().item()
    ses_error = ses_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    ses_abs_error = abs(ses_error)
    ses_preds1.append(ses_pred)
    ses_errors.append(ses_abs_error)
    
    holt_model = Holt(gold['y'][:-gold_forecasting_horizon+i])
    holt_model_fit = holt_model.fit()
    holt_pred = holt_model_fit.forecast(1).to_numpy().item()
    holt_error = holt_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    holt_abs_error = abs(holt_error)
    holt_preds1.append(holt_pred)
    holt_errors.append(holt_abs_error)
    
    hw_model = ExponentialSmoothing(gold['y'][:-gold_forecasting_horizon+i], seasonal_periods=5, trend='add', seasonal='add')
    hw_model_fit = hw_model.fit()
    hw_pred = hw_model_fit.forecast(1).to_numpy().item()
    hw_error = hw_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    hw_abs_error = abs(hw_error)
    hw_preds1.append(hw_pred)
    hw_errors.append(hw_abs_error)
    
ses_abs_errors = np.array(ses_errors)
ses = ses_abs_errors.mean()
holt_abs_errors = np.array(holt_errors)
holt = holt_abs_errors.mean()
hw_abs_errors = np.array(hw_errors)
hw = hw_abs_errors.mean()

results['Simple Exponential Smoothing'].iloc[0] = ses
results['Holt\'s Exponential Smoothing'].iloc[0] = holt
results['Holt-Winter\'s Exponential Smoothing'].iloc[0] = hw

In [11]:
#prophet
prophet_errors = []
prophet_preds1 = []
#prophet-ARIMA
prophet_arima_errors = []
prophet_arima_preds1 = []

for i in range(gold_forecasting_horizon) :
    date = gold['ds'].iloc[gold.shape[0]-gold_forecasting_horizon+i] - gold['ds'].iloc[gold.shape[0]-gold_forecasting_horizon+i-1]
    m = Prophet()
    m.fit(gold.iloc[:gold.shape[0]-gold_forecasting_horizon+i])
    future = m.make_future_dataframe(periods=date.days)
    forecast = m.predict(future)
    prophet_pred = forecast['yhat'].iloc[-1]
    prophet_error = prophet_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    prophet_abs_error = abs(prophet_error)
    prophet_preds1.append(prophet_pred)
    prophet_errors.append(prophet_abs_error)
    
    
    error_series = gold['y'][:gold.shape[0]-gold_forecasting_horizon+i] - forecast['yhat'].iloc[:-date.days]
    prophet_arima_model = pm.auto_arima(error_series, start_p = 0, start_q = 0, max_p = 5, max_q = 5, \
                                        seasonal = False, information_criteria = 'bic')
    prophet_arima_pred = prophet_arima_model.predict(n_periods=1).to_numpy().item() + prophet_pred
    prophet_arima_error = prophet_arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    prophet_arima_abs_error = abs(prophet_arima_error)
    prophet_arima_preds1.append(prophet_arima_pred)
    prophet_arima_errors.append(prophet_arima_abs_error)    

    
prophet_abs_errors = np.array(prophet_errors)
prophet = prophet_abs_errors.mean()
prophet_arima_abs_errors = np.array(prophet_arima_errors)
prophet_arima = prophet_arima_abs_errors.mean()

results['Prophet'].iloc[0] = prophet
results['Prophet+ARIMA'].iloc[0] = prophet_arima

20:13:04 - cmdstanpy - INFO - Chain [1] start processing
20:13:04 - cmdstanpy - INFO - Chain [1] done processing
20:13:05 - cmdstanpy - INFO - Chain [1] start processing
20:13:06 - cmdstanpy - INFO - Chain [1] done processing
20:13:07 - cmdstanpy - INFO - Chain [1] start processing
20:13:07 - cmdstanpy - INFO - Chain [1] done processing
20:13:09 - cmdstanpy - INFO - Chain [1] start processing
20:13:09 - cmdstanpy - INFO - Chain [1] done processing
20:13:10 - cmdstanpy - INFO - Chain [1] start processing
20:13:11 - cmdstanpy - INFO - Chain [1] done processing
20:13:12 - cmdstanpy - INFO - Chain [1] start processing
20:13:12 - cmdstanpy - INFO - Chain [1] done processing
20:13:13 - cmdstanpy - INFO - Chain [1] start processing
20:13:13 - cmdstanpy - INFO - Chain [1] done processing
20:13:15 - cmdstanpy - INFO - Chain [1] start processing
20:13:15 - cmdstanpy - INFO - Chain [1] done processing
20:13:16 - cmdstanpy - INFO - Chain [1] start processing
20:13:17 - cmdstanpy - INFO - Chain [1]

20:15:11 - cmdstanpy - INFO - Chain [1] done processing
20:15:12 - cmdstanpy - INFO - Chain [1] start processing
20:15:13 - cmdstanpy - INFO - Chain [1] done processing
20:15:14 - cmdstanpy - INFO - Chain [1] start processing
20:15:15 - cmdstanpy - INFO - Chain [1] done processing
20:15:16 - cmdstanpy - INFO - Chain [1] start processing
20:15:17 - cmdstanpy - INFO - Chain [1] done processing
20:15:18 - cmdstanpy - INFO - Chain [1] start processing
20:15:18 - cmdstanpy - INFO - Chain [1] done processing
20:15:20 - cmdstanpy - INFO - Chain [1] start processing
20:15:20 - cmdstanpy - INFO - Chain [1] done processing
20:15:22 - cmdstanpy - INFO - Chain [1] start processing
20:15:22 - cmdstanpy - INFO - Chain [1] done processing
20:15:24 - cmdstanpy - INFO - Chain [1] start processing
20:15:24 - cmdstanpy - INFO - Chain [1] done processing
20:15:25 - cmdstanpy - INFO - Chain [1] start processing
20:15:26 - cmdstanpy - INFO - Chain [1] done processing
20:15:27 - cmdstanpy - INFO - Chain [1] 

In [12]:
gold_pred =pd.DataFrame(index= gold['ds'][-gold_forecasting_horizon:], columns=columns)
gold_pred['Actual'] = list(gold['y'][gold.shape[0]-gold_forecasting_horizon:])
gold_pred['ARIMA'] = arima_preds1
gold_pred['ARIMA-GARCH'] = arch_preds1
gold_pred['ARIMA 2'] = arima_preds2_1
gold_pred['ARIMA-GARCH 2'] = arch_preds2_1
gold_pred['ARIMA 3'] = arima_preds3_1
gold_pred['ARIMA-GARCH 3'] = arch_preds3_1
gold_pred['Simple Exponential Smoothing'] = ses_preds1
gold_pred['Holt\'s Exponential Smoothing'] = holt_preds1
gold_pred['Holt-Winter\'s Exponential Smoothing'] = hw_preds1
gold_pred['Prophet'] = prophet_preds1
gold_pred['Prophet+ARIMA'] = prophet_arima_preds1
gold_pred.to_csv('./results/gold_1step_forecasting.csv')

In [13]:
results.to_csv('./results/mae.csv')

### Gold (5-step)

In [14]:
#ARIMA(0,1,0)
arima_errors = []
arima_preds5 = []
#ARIMA(0,1,0)-GARCH(1,1)
arch_errors = []
arch_preds5 = []
order = (0,1,0)


for i in range(gold_forecasting_horizon) :
    arima_model = ARIMA(gold['y'][:gold.shape[0]-gold_forecasting_horizon-4+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=5).iloc[-1]
    arima_error = arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds5.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=5).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=5)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds5.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA'].iloc[1] = arima
results['ARIMA-GARCH'].iloc[1] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39146.510773923284
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7633.792832765138
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4638.409347675435
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6224.168831680647
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4626.235512794343
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4624.316429868677
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4624.1107411949015
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4623.816615368818
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4623.4994852684185
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4623.310660093545
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4623.283892846169
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4623.283762647172
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4623.283759317207
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4623.28

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39206.87825757309
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7653.203072565611
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4650.348921601352
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6246.461337589249
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4638.021924193354
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4635.987942148798
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4635.781537433482
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4635.496219015795
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4635.188050807462
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4635.010538274331
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4634.985738413041
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4634.985632905799
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4634.985630526269
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4634.98563

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39414.19665960208
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7680.7034801232
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4664.546124613158
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6263.831010007256
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4652.3668801450585
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4650.089408123231
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4649.9061366513615
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4649.625487195113
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4649.352390205151
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4649.2035771157625
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4649.186553133297
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4649.186492095692
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4649.186490646749
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4649.1864

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 43843.7307898736
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8451.17671419567
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5158.297623860726
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5484.580804425711
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5144.259887367251
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5144.207306653931
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5144.150782137057
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5144.028247277829
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5144.00148552472
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5143.998215465639
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5143.998178335287
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5143.998178335476
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5143.998178335287
            Iterations: 12
    

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 43855.48735500442
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8469.858793477131
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5170.186018970345
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5464.358251241946
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5155.846137658544
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5155.7944837153245
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5155.731723101999
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5155.612802341198
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5155.584157145646
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5155.580669906681
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5155.580620799102
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5155.580620799248
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5155.580620799102
            Iterations: 12


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

In [15]:
#ARIMA(2,1,2)
arima_errors = []
arima_preds2_5 = []
#ARIMA(2,1,2)-GARCH(1,1)
arch_errors = []
arch_preds2_5 = []
order = (2,1,2)


for i in range(gold_forecasting_horizon) :
    arima_model = ARIMA(gold['y'][:gold.shape[0]-gold_forecasting_horizon-4+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=5).iloc[-1]
    arima_error = arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds2_5.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=5).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=5)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds2_5.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 2'].iloc[1] = arima
results['ARIMA-GARCH 2'].iloc[1] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39117.909227286524
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7635.1105256440605
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4638.076469873281
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6052.262622319314
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4625.246320880349
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4623.29971940125
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4623.128765151176
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4622.716612150676
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4622.463040204968
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4622.340209544044
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4622.337458287291
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4622.3374448521845
Iteration:     13,   Func. Count:     71,   Neg. LLF: 4622.337444852013
Optimization terminated successfully    (Exit mode 0)
        

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 39154.14105139686
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7640.004436489289
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4642.4272276586635
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6104.967193501198
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4629.553007631535
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4627.725300186174
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4627.52879672351
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4627.133933578899
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4626.845084512504
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4626.693052733325
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4626.685790138248
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4626.68575003928
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4626.685749208224
Optimization terminated successfully    (Exit mode 0)
           

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 39285.28450235218
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7647.294360030348
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4646.362701337333
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6089.623408567055
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4633.387000768452
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4631.421421799419
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4631.236422043554
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4630.8317351174155
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4630.564117149997
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4630.4310361415355
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4630.426731844878
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4630.42670974205
Iteration:     13,   Func. Count:     71,   Neg. LLF: 4630.426709741854
Optimization terminated successfully    (Exit mode 0)
         

...

C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting 

Iteration:      1,   Func. Count:      6,   Neg. LLF: 43927.93107007293
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8471.734162208435
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5171.430741722035
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5303.900613085452
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5156.5097874831445
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5156.466023337351
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5156.388230437254
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5156.28226472662
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5156.249474210573
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5156.245820584738
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5156.245729698059
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5156.245729698125
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5156.245729698059
            Iterations: 12
 

C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting 

Iteration:      1,   Func. Count:      6,   Neg. LLF: 43993.86910265985
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8479.14742599596
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5175.445781204571
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5301.60258011804
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5160.496011529005
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5160.45149467024
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5160.3719959791215
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5160.264143924004
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5160.230735660703
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5160.227045031749
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5160.2269539328245
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5160.226953932899
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5160.2269539328245
            Iterations: 12
 

C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [16]:
#ARIMA(1,1,0)
arima_errors = []
arima_preds3_5 = []
#ARIMA(1,1,0)-GARCH(1,1)
arch_errors = []
arch_preds3_5 = []
order = (1,1,0)


for i in range(gold_forecasting_horizon) :
    arima_model = ARIMA(gold['y'][:gold.shape[0]-gold_forecasting_horizon-4+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=5).iloc[-1]
    arima_error = arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds3_5.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=5).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=5)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds3_5.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 3'].iloc[1] = arima
results['ARIMA-GARCH 3'].iloc[1] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39158.59697792279
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7633.427207878994
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4637.77169020767
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6213.463588943585
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4625.561603269425
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4623.5522713035225
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4623.349443831224
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4623.009059760499
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4622.700353807857
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4622.524642297731
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4622.507848895215
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4622.507763989926
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4622.50776171928
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4622.507761

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 39144.066544093046
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7645.765085072611
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4645.992286243055
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6244.724006001211
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4633.622528530399
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4631.620212494772
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4631.404487374563
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4631.073584961037
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4630.756812964731
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4630.577441302571
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4630.558203115088
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4630.558109985656
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4630.558107858113
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4630.5581

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 39353.15924257478
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7659.8894499003745
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4653.284001395845
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6227.265031777996
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4640.93186347182
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4638.713268781978
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4638.521235161062
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4638.188924285129
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4637.906886668799
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4637.755842525962
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4637.743592793473
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4637.743543564586
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4637.7435423042625
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4637.7435

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 43824.50727808629
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8457.741353387835
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5161.964105195942
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5493.531714886029
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5147.752174783748
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5147.6984114328925
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5147.636155559113
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5147.512575834962
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5147.48385800413
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5147.4803820871675
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5147.480334834159
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5147.4803348343185
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5147.480334834159
            Iterations: 12

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 43979.82812694901
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8469.633783504976
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5169.776052239888
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5481.03582911973
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5155.427029763186
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5155.374657911149
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5155.310826610255
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5155.1912181848365
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5155.1625651919585
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5155.159092592175
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5155.159042555449
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5155.159042555684
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5155.159042555449
            Iterations: 12


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

In [17]:
#SES
ses_errors = []
ses_preds5 = []
#Holt
holt_errors = []
holt_preds5 = []
#Holt-Winter
hw_errors = []
hw_preds5 = []

for i in range(gold_forecasting_horizon) :
    ses_model = SimpleExpSmoothing(gold['y'][:-gold_forecasting_horizon-4+i])
    ses_model_fit = ses_model.fit()
    ses_pred = ses_model_fit.forecast(5).iloc[-1]
    ses_error = ses_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    ses_abs_error = abs(ses_error)
    ses_preds5.append(ses_pred)
    ses_errors.append(ses_abs_error)
    
    holt_model = Holt(gold['y'][:-gold_forecasting_horizon-4+i])
    holt_model_fit = holt_model.fit()
    holt_pred = holt_model_fit.forecast(5).iloc[-1]
    holt_error = holt_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    holt_abs_error = abs(holt_error)
    holt_preds5.append(holt_pred)
    holt_errors.append(holt_abs_error)
    
    hw_model = ExponentialSmoothing(gold['y'][:-gold_forecasting_horizon-4+i], seasonal_periods=5, trend='add', seasonal='add')
    hw_model_fit = hw_model.fit()
    hw_pred = hw_model_fit.forecast(5).iloc[-1]
    hw_error = hw_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    hw_abs_error = abs(hw_error)
    hw_preds5.append(hw_pred)
    hw_errors.append(hw_abs_error)
    
ses_abs_errors = np.array(ses_errors)
ses = ses_abs_errors.mean()
holt_abs_errors = np.array(holt_errors)
holt = holt_abs_errors.mean()
hw_abs_errors = np.array(hw_errors)
hw = hw_abs_errors.mean()

results['Simple Exponential Smoothing'].iloc[1] = ses
results['Holt\'s Exponential Smoothing'].iloc[1] = holt
results['Holt-Winter\'s Exponential Smoothing'].iloc[1] = hw

In [18]:
#prophet
prophet_errors = []
prophet_preds5 = []
#prophet-ARIMA
prophet_arima_errors = []
prophet_arima_preds5 = []

for i in range(gold_forecasting_horizon) :
    date = gold['ds'].iloc[gold.shape[0]-gold_forecasting_horizon+i] - gold['ds'].iloc[gold.shape[0]-gold_forecasting_horizon-5+i]
    m = Prophet()
    m.fit(gold.iloc[:gold.shape[0]-gold_forecasting_horizon-4+i])
    future = m.make_future_dataframe(periods=date.days)
    forecast = m.predict(future)
    prophet_pred = forecast['yhat'].iloc[-1]
    prophet_error = prophet_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    prophet_abs_error = abs(prophet_error)
    prophet_preds5.append(prophet_pred)
    prophet_errors.append(prophet_abs_error)
    
    
    error_series = gold['y'][:gold.shape[0]-gold_forecasting_horizon-4+i] - forecast['yhat'].iloc[:-date.days]
    prophet_arima_model = pm.auto_arima(error_series, start_p = 0, start_q = 0, max_p = 5, max_q = 5, \
                                        seasonal = False, information_criteria = 'bic')
    prophet_arima_pred = prophet_arima_model.predict(n_periods=5).iloc[-1].item() + prophet_pred
    prophet_arima_error = prophet_arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    prophet_arima_abs_error = abs(prophet_arima_error)
    prophet_arima_preds5.append(prophet_arima_pred)
    prophet_arima_errors.append(prophet_arima_abs_error)    

    
prophet_abs_errors = np.array(prophet_errors)
prophet = prophet_abs_errors.mean()
prophet_arima_abs_errors = np.array(prophet_arima_errors)
prophet_arima = prophet_arima_abs_errors.mean()

results['Prophet'].iloc[1] = prophet
results['Prophet+ARIMA'].iloc[1] = prophet_arima

20:19:50 - cmdstanpy - INFO - Chain [1] start processing
20:19:51 - cmdstanpy - INFO - Chain [1] done processing
20:19:52 - cmdstanpy - INFO - Chain [1] start processing
20:19:53 - cmdstanpy - INFO - Chain [1] done processing
20:19:54 - cmdstanpy - INFO - Chain [1] start processing
20:19:54 - cmdstanpy - INFO - Chain [1] done processing
20:19:56 - cmdstanpy - INFO - Chain [1] start processing
20:19:56 - cmdstanpy - INFO - Chain [1] done processing
20:19:57 - cmdstanpy - INFO - Chain [1] start processing
20:19:58 - cmdstanpy - INFO - Chain [1] done processing
20:19:59 - cmdstanpy - INFO - Chain [1] start processing
20:19:59 - cmdstanpy - INFO - Chain [1] done processing
20:20:01 - cmdstanpy - INFO - Chain [1] start processing
20:20:01 - cmdstanpy - INFO - Chain [1] done processing
20:20:02 - cmdstanpy - INFO - Chain [1] start processing
20:20:03 - cmdstanpy - INFO - Chain [1] done processing
20:20:04 - cmdstanpy - INFO - Chain [1] start processing
20:20:04 - cmdstanpy - INFO - Chain [1]

20:21:53 - cmdstanpy - INFO - Chain [1] done processing
20:21:54 - cmdstanpy - INFO - Chain [1] start processing
20:21:54 - cmdstanpy - INFO - Chain [1] done processing
20:21:56 - cmdstanpy - INFO - Chain [1] start processing
20:21:56 - cmdstanpy - INFO - Chain [1] done processing
20:21:57 - cmdstanpy - INFO - Chain [1] start processing
20:21:58 - cmdstanpy - INFO - Chain [1] done processing
20:21:59 - cmdstanpy - INFO - Chain [1] start processing
20:22:00 - cmdstanpy - INFO - Chain [1] done processing
20:22:01 - cmdstanpy - INFO - Chain [1] start processing
20:22:02 - cmdstanpy - INFO - Chain [1] done processing
20:22:03 - cmdstanpy - INFO - Chain [1] start processing
20:22:03 - cmdstanpy - INFO - Chain [1] done processing
20:22:05 - cmdstanpy - INFO - Chain [1] start processing
20:22:05 - cmdstanpy - INFO - Chain [1] done processing
20:22:07 - cmdstanpy - INFO - Chain [1] start processing
20:22:07 - cmdstanpy - INFO - Chain [1] done processing
20:22:09 - cmdstanpy - INFO - Chain [1] 

In [19]:
gold_pred =pd.DataFrame(index= gold['ds'][-gold_forecasting_horizon:], columns=columns)
gold_pred['Actual'] = gold['y'][gold.shape[0]-gold_forecasting_horizon:]
gold_pred['ARIMA'] = arima_preds5
gold_pred['ARIMA-GARCH'] = arch_preds5
gold_pred['ARIMA 2'] = arima_preds2_5
gold_pred['ARIMA-GARCH 2'] = arch_preds2_5
gold_pred['ARIMA 3'] = arima_preds3_5
gold_pred['ARIMA-GARCH 3'] = arch_preds3_5
gold_pred['Simple Exponential Smoothing'] = ses_preds5
gold_pred['Holt\'s Exponential Smoothing'] = holt_preds5
gold_pred['Holt-Winter\'s Exponential Smoothing'] = hw_preds5
gold_pred['Prophet'] = prophet_preds5
gold_pred['Prophet+ARIMA'] = prophet_arima_preds5
gold_pred.to_csv('./results/gold_5step_forecasting.csv')

In [20]:
results.to_csv('./results/mae.csv')

### Gold (10 step)

In [21]:
#ARIMA(0,1,0)
arima_errors = []
arima_preds10 = []
#ARIMA(0,1,0)-GARCH(1,1)
arch_errors = []
arch_preds10 = []
order = (0,1,0)


for i in range(gold_forecasting_horizon) :
    arima_model = ARIMA(gold['y'][:gold.shape[0]-gold_forecasting_horizon-9+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=10).iloc[-1]
    arima_error = arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds10.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=10).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=10)
    predicted_et = garch_forecast.mean['h.01'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds10.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA'].iloc[2] = arima
results['ARIMA-GARCH'].iloc[2] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 38903.609248452245
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7600.567745968114
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4618.742773601517
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6189.470970413555
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4605.39243387213
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4604.366704993639
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4604.085097375921
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4603.647964620604
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4603.261577102919
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4603.031507035312
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4603.014702207935
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4603.014536019005
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4603.014532741257
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4603.01453

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 38946.9840011357
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7620.077908906476
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4631.035110737616
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6251.887469381139
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4618.467562586343
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4616.886002257375
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4616.632413548503
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4616.289633515569
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4615.919968288468
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4615.6957137988375
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4615.665773167602
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4615.665581871885
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4615.665577263
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4615.66557726

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 39217.01481643638
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7646.170417762198
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4646.667837326362
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6256.621184926369
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4634.329674179477
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4632.430707623862
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4632.210176518836
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4631.924371601107
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4631.598282872624
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4631.407015692349
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4631.377706798169
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4631.3775762610185
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4631.377573510303
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4631.3775

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 43804.34516620898
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8429.970921344731
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5143.4162032254535
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5895.708094388077
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5128.968360880645
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5128.910285236901
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5128.837575372554
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5128.706130905844
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5128.673254698089
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5128.669271996951
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5128.669214211714
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5128.669214211902
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5128.669214211714
            Iterations: 12


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 43843.7307898736
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8451.17671419567
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5158.297623860726
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5484.580804425711
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5144.259887367251
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5144.207306653931
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5144.150782137057
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5144.028247277829
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5144.00148552472
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5143.998215465639
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5143.998178335287
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5143.998178335476
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5143.998178335287
            Iterations: 12
    

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [22]:
#ARIMA(2,1,2)
arima_errors = []
arima_preds2_10 = []
#ARIMA(2,1,2)-GARCH(1,1)
arch_errors = []
arch_preds2_10 = []
order = (2,1,2)


for i in range(gold_forecasting_horizon) :
    arima_model = ARIMA(gold['y'][:gold.shape[0]-gold_forecasting_horizon-9+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=10).iloc[-1]
    arima_error = arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds2_10.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=10).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=10)
    predicted_et = garch_forecast.mean['h.01'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds2_10.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 2'].iloc[2] = arima
results['ARIMA-GARCH 2'].iloc[2] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 38839.587500136084
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7601.129959559084
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4618.547801518322
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6135.466732583002
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4606.912382059878
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4604.7876774102415
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4604.61549265809
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4604.482752795957
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4604.2180079148575
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4604.0557277381195
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4604.006238527374
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4604.005698205644
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4604.0056976051455
Optimization terminated successfully    (Exit mode 0)
      

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 38870.67350204943
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7606.953701066886
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4622.654382190244
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6187.466448126537
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4611.472885987014
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4609.063663720301
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4608.887368019205
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4608.763918660471
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4608.498908721417
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4608.341693671098
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4608.29249435795
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4608.29199453728
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4608.291993676464
Optimization terminated successfully    (Exit mode 0)
            

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 38918.43378927185
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7613.7759712870875
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4626.813097909671
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6198.672867433035
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4615.973166419858
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4613.208237641163
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4613.043762857271
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4612.929831473069
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4612.677140119894
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4612.530236182041
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4612.483378636236
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4612.48289126079
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4612.48289078403
Optimization terminated successfully    (Exit mode 0)
           

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood o

Iteration:      1,   Func. Count:      6,   Neg. LLF: 43837.32660692783
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8436.99695637741
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5144.056878636553
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6181.614692831774
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5129.867882410719
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5129.810905854491
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5129.745971484915
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5129.61465572243
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5129.58331942242
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5129.5793558080995
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5129.57931003909
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5129.579310039344
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5129.57931003909
            Iterations: 12
     

C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting 

Iteration:      1,   Func. Count:      6,   Neg. LLF: 43837.83765977887
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8444.346830155642
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5153.1430428943595
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5436.331036868056
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5138.143232667805
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5138.094557542056
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5138.011723116547
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5137.895701209429
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5137.860631083641
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5137.856683634751
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5137.856592908858
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5137.856592908878
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5137.856592908858
            Iterations: 12


C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [23]:
#ARIMA(1,1,0)
arima_errors = []
arima_preds3_10 = []
#ARIMA(1,1,0)-GARCH(1,1)
arch_errors = []
arch_preds3_10 = []
order = (1,1,0)

for i in range(gold_forecasting_horizon) :
    arima_model = ARIMA(gold['y'][:gold.shape[0]-gold_forecasting_horizon-9+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=10).iloc[9]
    arima_error = arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds3_10.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=10).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=10)
    predicted_et = garch_forecast.mean['h.01'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds3_10.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 3'].iloc[2] = arima
results['ARIMA-GARCH 3'].iloc[2] = arch

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 38907.88729739196
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7600.186229542312
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4618.130351344697
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6181.130580002178
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4604.708842846112
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4603.631612263247
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4603.35036887277
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4602.861849636642
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4602.486065623009
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4602.27534031329
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4602.265963866056
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4602.265851702786
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4602.265850204837
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4602.2658502

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 38906.38300287936
Iteration:      2,   Func. Count:     12,   Neg. LLF: 7613.625331069528
Iteration:      3,   Func. Count:     19,   Neg. LLF: 4626.578439414019
Iteration:      4,   Func. Count:     25,   Neg. LLF: 6218.066229333902
Iteration:      5,   Func. Count:     31,   Neg. LLF: 4613.595463872304
Iteration:      6,   Func. Count:     37,   Neg. LLF: 4612.117445876418
Iteration:      7,   Func. Count:     42,   Neg. LLF: 4611.854814855744
Iteration:      8,   Func. Count:     47,   Neg. LLF: 4611.420349550888
Iteration:      9,   Func. Count:     52,   Neg. LLF: 4611.050503503146
Iteration:     10,   Func. Count:     57,   Neg. LLF: 4610.837583334154
Iteration:     11,   Func. Count:     62,   Neg. LLF: 4610.82261081577
Iteration:     12,   Func. Count:     67,   Neg. LLF: 4610.822474434385
Iteration:     13,   Func. Count:     72,   Neg. LLF: 4610.822471891357
Iteration:     14,   Func. Count:     76,   Neg. LLF: 4610.822471

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 43726.26604122642
Iteration:      2,   Func. Count:     12,   Neg. LLF: 8435.854051504939
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5147.512541739245
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5798.989111341787
Iteration:      5,   Func. Count:     33,   Neg. LLF: 5133.023257053372
Iteration:      6,   Func. Count:     38,   Neg. LLF: 5132.9644337914015
Iteration:      7,   Func. Count:     43,   Neg. LLF: 5132.889835493497
Iteration:      8,   Func. Count:     48,   Neg. LLF: 5132.757425868973
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5132.724663022107
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5132.720756708359
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5132.7206992089195
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5132.720699209127
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5132.7206992089195
            Iterations: 1

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      8,   Func. Count:     48,   Neg. LLF: 5143.569137874317
Iteration:      9,   Func. Count:     53,   Neg. LLF: 5143.542243061362
Iteration:     10,   Func. Count:     58,   Neg. LLF: 5143.539010666869
Iteration:     11,   Func. Count:     63,   Neg. LLF: 5143.538973736471
Iteration:     12,   Func. Count:     67,   Neg. LLF: 5143.538973736625
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5143.538973736471
            Iterations: 12
            Function evaluations: 67
            Gradient evaluations: 12


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [24]:
#SES
ses_errors = []
ses_preds10 = []
#Holt
holt_errors = []
holt_preds10 = []
#Holt-Winter
hw_errors = []
hw_preds10 = []

for i in range(gold_forecasting_horizon) :
    ses_model = SimpleExpSmoothing(gold['y'][:-gold_forecasting_horizon-9+i])
    ses_model_fit = ses_model.fit()
    ses_pred = ses_model_fit.forecast(10).iloc[9]
    ses_error = ses_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    ses_abs_error = abs(ses_error)
    ses_preds10.append(ses_pred)
    ses_errors.append(ses_abs_error)
    
    holt_model = Holt(gold['y'][:-gold_forecasting_horizon-9+i])
    holt_model_fit = holt_model.fit()
    holt_pred = holt_model_fit.forecast(10).iloc[9]
    holt_error = holt_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    holt_abs_error = abs(holt_error)
    holt_preds10.append(holt_pred)
    holt_errors.append(holt_abs_error)
    
    hw_model = ExponentialSmoothing(gold['y'][:-gold_forecasting_horizon-9+i], seasonal_periods=5, trend='add', seasonal='add')
    hw_model_fit = hw_model.fit()
    hw_pred = hw_model_fit.forecast(10).iloc[9]
    hw_error = hw_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    hw_abs_error = abs(hw_error)
    hw_preds10.append(hw_pred)
    hw_errors.append(hw_abs_error)
    
ses_abs_errors = np.array(ses_errors)
ses = ses_abs_errors.mean()
holt_abs_errors = np.array(holt_errors)
holt = holt_abs_errors.mean()
hw_abs_errors = np.array(hw_errors)
hw = hw_abs_errors.mean()

results['Simple Exponential Smoothing'].iloc[2] = ses
results['Holt\'s Exponential Smoothing'].iloc[2] = holt
results['Holt-Winter\'s Exponential Smoothing'].iloc[2] = hw

In [25]:
#prophet
prophet_errors = []
prophet_preds10 = []
#prophet-ARIMA
prophet_arima_errors = []
prophet_arima_preds10 = []

for i in range(gold_forecasting_horizon) :
    date = gold['ds'].iloc[gold.shape[0]-gold_forecasting_horizon+i] - gold['ds'].iloc[gold.shape[0]-gold_forecasting_horizon-10+i]
    m = Prophet()
    m.fit(gold.iloc[:gold.shape[0]-gold_forecasting_horizon-9+i])
    future = m.make_future_dataframe(periods=date.days)
    forecast = m.predict(future)
    prophet_pred = forecast['yhat'].iloc[-1]
    prophet_error = prophet_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    prophet_abs_error = abs(prophet_error)
    prophet_preds10.append(prophet_pred)
    prophet_errors.append(prophet_abs_error)
    
    
    error_series = gold['y'][:gold.shape[0]-gold_forecasting_horizon-9+i] - forecast['yhat'].iloc[:-date.days]
    prophet_arima_model = pm.auto_arima(error_series, start_p = 0, start_q = 0, max_p = 5, max_q = 5, \
                                        seasonal = False, information_criteria = 'bic')
    prophet_arima_pred = prophet_arima_model.predict(n_periods=10).iloc[-1].item() + prophet_pred
    prophet_arima_error = prophet_arima_pred - gold['y'][gold.shape[0]-gold_forecasting_horizon+i]
    prophet_arima_abs_error = abs(prophet_arima_error)
    prophet_arima_preds10.append(prophet_arima_pred)
    prophet_arima_errors.append(prophet_arima_abs_error)    

    
prophet_abs_errors = np.array(prophet_errors)
prophet = prophet_abs_errors.mean()
prophet_arima_abs_errors = np.array(prophet_arima_errors)
prophet_arima = prophet_arima_abs_errors.mean()

results['Prophet'].iloc[2] = prophet
results['Prophet+ARIMA'].iloc[2] = prophet_arima

20:26:33 - cmdstanpy - INFO - Chain [1] start processing
20:26:33 - cmdstanpy - INFO - Chain [1] done processing
20:26:34 - cmdstanpy - INFO - Chain [1] start processing
20:26:35 - cmdstanpy - INFO - Chain [1] done processing
20:26:36 - cmdstanpy - INFO - Chain [1] start processing
20:26:36 - cmdstanpy - INFO - Chain [1] done processing
20:26:37 - cmdstanpy - INFO - Chain [1] start processing
20:26:38 - cmdstanpy - INFO - Chain [1] done processing
20:26:39 - cmdstanpy - INFO - Chain [1] start processing
20:26:39 - cmdstanpy - INFO - Chain [1] done processing
20:26:41 - cmdstanpy - INFO - Chain [1] start processing
20:26:41 - cmdstanpy - INFO - Chain [1] done processing
20:26:42 - cmdstanpy - INFO - Chain [1] start processing
20:26:43 - cmdstanpy - INFO - Chain [1] done processing
20:26:44 - cmdstanpy - INFO - Chain [1] start processing
20:26:44 - cmdstanpy - INFO - Chain [1] done processing
20:26:46 - cmdstanpy - INFO - Chain [1] start processing
20:26:46 - cmdstanpy - INFO - Chain [1]

20:28:32 - cmdstanpy - INFO - Chain [1] done processing
20:28:34 - cmdstanpy - INFO - Chain [1] start processing
20:28:34 - cmdstanpy - INFO - Chain [1] done processing
20:28:35 - cmdstanpy - INFO - Chain [1] start processing
20:28:35 - cmdstanpy - INFO - Chain [1] done processing
20:28:37 - cmdstanpy - INFO - Chain [1] start processing
20:28:37 - cmdstanpy - INFO - Chain [1] done processing
20:28:39 - cmdstanpy - INFO - Chain [1] start processing
20:28:39 - cmdstanpy - INFO - Chain [1] done processing
20:28:40 - cmdstanpy - INFO - Chain [1] start processing
20:28:41 - cmdstanpy - INFO - Chain [1] done processing
20:28:42 - cmdstanpy - INFO - Chain [1] start processing
20:28:43 - cmdstanpy - INFO - Chain [1] done processing
20:28:44 - cmdstanpy - INFO - Chain [1] start processing
20:28:45 - cmdstanpy - INFO - Chain [1] done processing
20:28:46 - cmdstanpy - INFO - Chain [1] start processing
20:28:46 - cmdstanpy - INFO - Chain [1] done processing
20:28:48 - cmdstanpy - INFO - Chain [1] 

In [26]:
gold_pred =pd.DataFrame(index= gold['ds'][-gold_forecasting_horizon:], columns=columns)
gold_pred['Actual'] = gold['y'][gold.shape[0]-gold_forecasting_horizon:]
gold_pred['ARIMA'] = arima_preds10
gold_pred['ARIMA-GARCH'] = arch_preds10
gold_pred['ARIMA 2'] = arima_preds2_10
gold_pred['ARIMA-GARCH 2'] = arch_preds2_10
gold_pred['ARIMA 3'] = arima_preds3_10
gold_pred['ARIMA-GARCH 3'] = arch_preds3_10
gold_pred['Simple Exponential Smoothing'] = ses_preds10
gold_pred['Holt\'s Exponential Smoothing'] = holt_preds10
gold_pred['Holt-Winter\'s Exponential Smoothing'] = hw_preds10
gold_pred['Prophet'] = prophet_preds10
gold_pred['Prophet+ARIMA'] = prophet_arima_preds10
gold_pred.to_csv('./results/gold_10step_forecasting.csv')

In [27]:
results.to_csv('./results/mae.csv')

### Silver (1 step)

In [28]:
#ARIMA(1,1,0)
arima_errors = []
arima_preds1 = []
#ARIMA(1,1,0)-GARCH(1,1)
arch_errors = []
arch_preds1 = []
order = (1,1,0)


for i in range(silver_forecasting_horizon) :
    arima_model = ARIMA(silver['y'][:silver.shape[0]-silver_forecasting_horizon+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=1).to_numpy().item()
    arima_error = arima_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds1.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=1).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=1)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds1.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA'].iloc[3] = arima
results['ARIMA-GARCH'].iloc[3] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 588440378.619823
Iteration:      2,   Func. Count:     17,   Neg. LLF: 20153647.54173018
Iteration:      3,   Func. Count:     24,   Neg. LLF: 307.8900186105019
Iteration:      4,   Func. Count:     30,   Neg. LLF: 279.804670880419
Iteration:      5,   Func. Count:     36,   Neg. LLF: 276.28250507620186
Iteration:      6,   Func. Count:     42,   Neg. LLF: 275.52802239040915
Iteration:      7,   Func. Count:     48,   Neg. LLF: 276.3912114900254
Iteration:      8,   Func. Count:     54,   Neg. LLF: 242.4135344657679
Iteration:      9,   Func. Count:     60,   Neg. LLF: 241.71657460450058
Iteration:     10,   Func. Count:     66,   Neg. LLF: 241.26610243725597
Iteration:     11,   Func. Count:     72,   Neg. LLF: 242.81962228054186
Iteration:     12,   Func. Count:     79,   Neg. LLF: 240.78888647394987
Iteration:     13,   Func. Count:     85,   Neg. LLF: 240.78359958156753
Iteration:     14,   Func. Count:     90,   Neg. LLF: 240.7

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:     10,   Func. Count:     66,   Neg. LLF: 241.93885551762355
Iteration:     11,   Func. Count:     72,   Neg. LLF: 241.97113024455643
Iteration:     12,   Func. Count:     78,   Neg. LLF: 241.3329240972653
Iteration:     13,   Func. Count:     84,   Neg. LLF: 241.32778632436305
Iteration:     14,   Func. Count:     89,   Neg. LLF: 241.32778557817412
Optimization terminated successfully    (Exit mode 0)
            Current function value: 241.32778557817412
            Iterations: 14
            Function evaluations: 89
            Gradient evaluations: 14
Iteration:      1,   Func. Count:      6,   Neg. LLF: 2103982176.9942517
Iteration:      2,   Func. Count:     17,   Neg. LLF: 622450953.0256739
Iteration:      3,   Func. Count:     24,   Neg. LLF: 308.94443083316094
Iteration:      4,   Func. Count:     30,   Neg. LLF: 280.4507919871061
Iteration:      5,   Func. Count:     36,   Neg. LLF: 277.02867399035756
Iteration:      6,   Func. Count:     42,   Neg. LLF: 276.40279

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 608588537.6541016
Iteration:      2,   Func. Count:     17,   Neg. LLF: 1008487.9208203704
Iteration:      3,   Func. Count:     24,   Neg. LLF: 309.05422721915113
Iteration:      4,   Func. Count:     30,   Neg. LLF: 280.3477635342688
Iteration:      5,   Func. Count:     36,   Neg. LLF: 276.982106799985
Iteration:      6,   Func. Count:     42,   Neg. LLF: 276.4444932126979
Iteration:      7,   Func. Count:     48,   Neg. LLF: 277.4443838686178
Iteration:      8,   Func. Count:     54,   Neg. LLF: 243.27292658062333
Iteration:      9,   Func. Count:     60,   Neg. LLF: 242.5926736429393
Iteration:     10,   Func. Count:     66,   Neg. LLF: 1046.1752751940778
Iteration:     11,   Func. Count:     74,   Neg. LLF: 241.5519076109046
Iteration:     12,   Func. Count:     79,   Neg. LLF: 241.5470697699973
Iteration:     13,   Func. Count:     84,   Neg. LLF: 241.54630399028918
Iteration:     14,   Func. Count:     89,   Neg. LLF: 241.54

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1272159241.3939362
Iteration:      2,   Func. Count:     16,   Neg. LLF: 1756007.2513689492
Iteration:      3,   Func. Count:     23,   Neg. LLF: 358.4965816730486
Iteration:      4,   Func. Count:     29,   Neg. LLF: 346.3694925037497
Iteration:      5,   Func. Count:     35,   Neg. LLF: 349.1116740457132
Iteration:      6,   Func. Count:     41,   Neg. LLF: 340.8754703344823
Iteration:      7,   Func. Count:     47,   Neg. LLF: 1548.3528888413102
Iteration:      8,   Func. Count:     53,   Neg. LLF: 312.85995785779255
Iteration:      9,   Func. Count:     59,   Neg. LLF: 305.7082343834589
Iteration:     10,   Func. Count:     65,   Neg. LLF: 354343059.7511899
Iteration:     11,   Func. Count:     72,   Neg. LLF: 307.45511033308253
Iteration:     12,   Func. Count:     79,   Neg. LLF: 305.4435376766454
Iteration:     13,   Func. Count:     85,   Neg. LLF: 305.40820886564256
Iteration:     14,   Func. Count:     89,   Neg. LLF: 305.

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1379209179556391.2
Iteration:      2,   Func. Count:     16,   Neg. LLF: 2746378.9612298533
Iteration:      3,   Func. Count:     23,   Neg. LLF: 357.89239210999966
Iteration:      4,   Func. Count:     29,   Neg. LLF: 346.06978125317454
Iteration:      5,   Func. Count:     35,   Neg. LLF: 350.5730038217154
Iteration:      6,   Func. Count:     41,   Neg. LLF: 340.6813111381149
Iteration:      7,   Func. Count:     47,   Neg. LLF: 1038.913551656304
Iteration:      8,   Func. Count:     53,   Neg. LLF: 312.1769006866134
Iteration:      9,   Func. Count:     59,   Neg. LLF: 305.5748342819518
Iteration:     10,   Func. Count:     65,   Neg. LLF: 336721775.1190639
Iteration:     11,   Func. Count:     72,   Neg. LLF: 307.4625354537186
Iteration:     12,   Func. Count:     78,   Neg. LLF: 305.2435048056985
Iteration:     13,   Func. Count:     83,   Neg. LLF: 305.2308866666559
Iteration:     14,   Func. Count:     88,   Neg. LLF: 305.23

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [29]:
#ARIMA(2,1,2)
arima_errors = []
arima_preds2_1 = []
#ARIMA(2,1,2)-GARCH(1,1)
arch_errors = []
arch_preds2_1 = []
order = (2,1,2)


for i in range(silver_forecasting_horizon) :
    arima_model = ARIMA(silver['y'][:silver.shape[0]-silver_forecasting_horizon+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=1).to_numpy().item()
    arima_error = arima_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds2_1.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=1).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=1)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds2_1.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 2'].iloc[3] = arima
results['ARIMA-GARCH 2'].iloc[3] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 1857858408756491.2
Iteration:      2,   Func. Count:     17,   Neg. LLF: 620182406.4787086
Iteration:      3,   Func. Count:     24,   Neg. LLF: 304.04584422182165
Iteration:      4,   Func. Count:     30,   Neg. LLF: 273.6414730788151
Iteration:      5,   Func. Count:     36,   Neg. LLF: 270.82861441727107
Iteration:      6,   Func. Count:     42,   Neg. LLF: 270.5659908951708
Iteration:      7,   Func. Count:     48,   Neg. LLF: 273.0295563626139
Iteration:      8,   Func. Count:     54,   Neg. LLF: 237.33413068876652
Iteration:      9,   Func. Count:     60,   Neg. LLF: 237.0602055537528
Iteration:     10,   Func. Count:     66,   Neg. LLF: 236.57777413037104
Iteration:     11,   Func. Count:     72,   Neg. LLF: 235.9405543665282
Iteration:     12,   Func. Count:     78,   Neg. LLF: 235.71581265251473
Iteration:     13,   Func. Count:     83,   Neg. LLF: 235.7045589658536
Iteration:     14,   Func. Count:     88,   Neg. LLF: 235.

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 638902444.7212014
Iteration:      2,   Func. Count:     17,   Neg. LLF: 1503110.477855873
Iteration:      3,   Func. Count:     24,   Neg. LLF: 304.9865710339681
Iteration:      4,   Func. Count:     30,   Neg. LLF: 273.7011425072611
Iteration:      5,   Func. Count:     36,   Neg. LLF: 270.9653626168112
Iteration:      6,   Func. Count:     42,   Neg. LLF: 270.7831179548604
Iteration:      7,   Func. Count:     48,   Neg. LLF: 272.9858601132335
Iteration:      8,   Func. Count:     54,   Neg. LLF: 237.4704682404241
Iteration:      9,   Func. Count:     60,   Neg. LLF: 237.1780981769257
Iteration:     10,   Func. Count:     66,   Neg. LLF: 240.6800837224091
Iteration:     11,   Func. Count:     73,   Neg. LLF: 236.45967233798967
Iteration:     12,   Func. Count:     79,   Neg. LLF: 235.74829168832204
Iteration:     13,   Func. Count:     84,   Neg. LLF: 235.74409506475538
Iteration:     14,   Func. Count:     89,   Neg. LLF: 235.744

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 2106715755.2103689
Iteration:      2,   Func. Count:     17,   Neg. LLF: 1424525.7645782
Iteration:      3,   Func. Count:     24,   Neg. LLF: 305.087596916945
Iteration:      4,   Func. Count:     30,   Neg. LLF: 274.07522369419627
Iteration:      5,   Func. Count:     36,   Neg. LLF: 271.4222065599051
Iteration:      6,   Func. Count:     42,   Neg. LLF: 271.152212957339
Iteration:      7,   Func. Count:     48,   Neg. LLF: 273.69100439458
Iteration:      8,   Func. Count:     54,   Neg. LLF: 237.94015419186442
Iteration:      9,   Func. Count:     60,   Neg. LLF: 237.60730352196404
Iteration:     10,   Func. Count:     66,   Neg. LLF: 236.9622066623667
Iteration:     11,   Func. Count:     72,   Neg. LLF: 236.173484578971
Iteration:     12,   Func. Count:     77,   Neg. LLF: 236.15646356251742
Iteration:     13,   Func. Count:     82,   Neg. LLF: 236.15925174965778
Iteration:     14,   Func. Count:     88,   Neg. LLF: 236.1533928

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 326863985.00492376
Iteration:      2,   Func. Count:     16,   Neg. LLF: 3493710.629952914
Iteration:      3,   Func. Count:     23,   Neg. LLF: 364.78929442583853
Iteration:      4,   Func. Count:     29,   Neg. LLF: 345.8228429557846
Iteration:      5,   Func. Count:     35,   Neg. LLF: 336.66287403378175
Iteration:      6,   Func. Count:     41,   Neg. LLF: 1733.2583050188541
Iteration:      7,   Func. Count:     47,   Neg. LLF: 335.94549252708987
Iteration:      8,   Func. Count:     53,   Neg. LLF: 302.8920722814653
Iteration:      9,   Func. Count:     58,   Neg. LLF: 303.0815082677751
Iteration:     10,   Func. Count:     64,   Neg. LLF: 2139.235582176157
Iteration:     11,   Func. Count:     71,   Neg. LLF: 1919.5741081614178
Iteration:     12,   Func. Count:     78,   Neg. LLF: 302.3059205684564
Iteration:     13,   Func. Count:     83,   Neg. LLF: 302.3057891071954
Iteration:     14,   Func. Count:     88,   Neg. LLF: 302.

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1433894392221840.0
Iteration:      2,   Func. Count:     16,   Neg. LLF: 684830210.5745097
Iteration:      3,   Func. Count:     23,   Neg. LLF: 366.45993864279944
Iteration:      4,   Func. Count:     29,   Neg. LLF: 346.0618583876076
Iteration:      5,   Func. Count:     35,   Neg. LLF: 336.23748513539084
Iteration:      6,   Func. Count:     41,   Neg. LLF: 374.02868749529887
Iteration:      7,   Func. Count:     47,   Neg. LLF: 335.81197942371756
Iteration:      8,   Func. Count:     53,   Neg. LLF: 307.36130460986817
Iteration:      9,   Func. Count:     59,   Neg. LLF: 302.71254270000475
Iteration:     10,   Func. Count:     65,   Neg. LLF: 1730.0400465523107
Iteration:     11,   Func. Count:     73,   Neg. LLF: 310.4506444826675
Iteration:     12,   Func. Count:     80,   Neg. LLF: 302.20354032248247
Iteration:     13,   Func. Count:     85,   Neg. LLF: 302.20347921839715
Iteration:     14,   Func. Count:     89,   Neg. LLF: 

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [30]:
#ARIMA(0,1,4)
arima_errors = []
arima_preds3_1 = []
#ARIMA(0,1,4)-GARCH(1,1)
arch_errors = []
arch_preds3_1 = []
order = (0,1,4)


for i in range(silver_forecasting_horizon) :
    arima_model = ARIMA(silver['y'][:silver.shape[0]-silver_forecasting_horizon+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=1).to_numpy().item()
    arima_error = arima_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds3_1.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=1).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=1)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds3_1.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 3'].iloc[3] = arima
results['ARIMA-GARCH 3'].iloc[3] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 475243980.672488
Iteration:      2,   Func. Count:     17,   Neg. LLF: 619198317.2688801
Iteration:      3,   Func. Count:     24,   Neg. LLF: 303.2955653063535
Iteration:      4,   Func. Count:     30,   Neg. LLF: 272.5215119712185
Iteration:      5,   Func. Count:     36,   Neg. LLF: 269.979634984543
Iteration:      6,   Func. Count:     42,   Neg. LLF: 269.49063693879526
Iteration:      7,   Func. Count:     48,   Neg. LLF: 272.79098094758285
Iteration:      8,   Func. Count:     54,   Neg. LLF: 237.2483530629218
Iteration:      9,   Func. Count:     60,   Neg. LLF: 237.1217086753163
Iteration:     10,   Func. Count:     66,   Neg. LLF: 236.25039433212726
Iteration:     11,   Func. Count:     72,   Neg. LLF: 238.5690111162386
Iteration:     12,   Func. Count:     79,   Neg. LLF: 235.728350573299
Iteration:     13,   Func. Count:     84,   Neg. LLF: 235.72780487789242
Iteration:     14,   Func. Count:     90,   Neg. LLF: 235.72126

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 198522736.55003065
Iteration:      2,   Func. Count:     17,   Neg. LLF: 1024425.68595268
Iteration:      3,   Func. Count:     24,   Neg. LLF: 303.6477066073433
Iteration:      4,   Func. Count:     30,   Neg. LLF: 272.5561872158644
Iteration:      5,   Func. Count:     36,   Neg. LLF: 270.13575597669495
Iteration:      6,   Func. Count:     42,   Neg. LLF: 269.6797206588002
Iteration:      7,   Func. Count:     48,   Neg. LLF: 272.79236865502287
Iteration:      8,   Func. Count:     54,   Neg. LLF: 237.44811410167893
Iteration:      9,   Func. Count:     60,   Neg. LLF: 237.2465126555091
Iteration:     10,   Func. Count:     66,   Neg. LLF: 236.36569327105332
Iteration:     11,   Func. Count:     72,   Neg. LLF: 236.38582020774135
Iteration:     12,   Func. Count:     78,   Neg. LLF: 235.76601128872807
Iteration:     13,   Func. Count:     83,   Neg. LLF: 235.76096388264148
Iteration:     14,   Func. Count:     88,   Neg. LLF: 235

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 349710403.4457566
Iteration:      2,   Func. Count:     17,   Neg. LLF: 1030600.2843501798
Iteration:      3,   Func. Count:     24,   Neg. LLF: 303.58466682115346
Iteration:      4,   Func. Count:     30,   Neg. LLF: 272.97315974411885
Iteration:      5,   Func. Count:     36,   Neg. LLF: 270.6695917776944
Iteration:      6,   Func. Count:     42,   Neg. LLF: 270.0175418719124
Iteration:      7,   Func. Count:     48,   Neg. LLF: 273.658365944458
Iteration:      8,   Func. Count:     54,   Neg. LLF: 237.96582880861843
Iteration:      9,   Func. Count:     60,   Neg. LLF: 237.6599231717582
Iteration:     10,   Func. Count:     66,   Neg. LLF: 236.9866956959297
Iteration:     11,   Func. Count:     72,   Neg. LLF: 246.2010859495373
Iteration:     12,   Func. Count:     79,   Neg. LLF: 236.22673617558638
Iteration:     13,   Func. Count:     84,   Neg. LLF: 236.2131274909243
Iteration:     14,   Func. Count:     89,   Neg. LLF: 236.21

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 2070820774.8265753
Iteration:      2,   Func. Count:     16,   Neg. LLF: 684116144.1907111
Iteration:      3,   Func. Count:     23,   Neg. LLF: 366.26966044455133
Iteration:      4,   Func. Count:     29,   Neg. LLF: 346.10444687926713
Iteration:      5,   Func. Count:     35,   Neg. LLF: 335.6394216533986
Iteration:      6,   Func. Count:     41,   Neg. LLF: 339.56589146090175
Iteration:      7,   Func. Count:     47,   Neg. LLF: 336.02672280530174
Iteration:      8,   Func. Count:     53,   Neg. LLF: 2986.7816468533215
Iteration:      9,   Func. Count:     59,   Neg. LLF: 303.3377387712346
Iteration:     10,   Func. Count:     64,   Neg. LLF: 535.6092485392281
Iteration:     11,   Func. Count:     71,   Neg. LLF: 1608.3068655424217
Iteration:     12,   Func. Count:     78,   Neg. LLF: 303.2051730313545
Iteration:     13,   Func. Count:     84,   Neg. LLF: 303.1072154884806
Iteration:     14,   Func. Count:     89,   Neg. LLF: 303

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1449317857996587.5
Iteration:      2,   Func. Count:     16,   Neg. LLF: 684304912.7176688
Iteration:      3,   Func. Count:     23,   Neg. LLF: 368.62819183802986
Iteration:      4,   Func. Count:     29,   Neg. LLF: 346.1636287879641
Iteration:      5,   Func. Count:     35,   Neg. LLF: 335.4795324610526
Iteration:      6,   Func. Count:     41,   Neg. LLF: 336.82151699705054
Iteration:      7,   Func. Count:     47,   Neg. LLF: 482.08140160047026
Iteration:      8,   Func. Count:     53,   Neg. LLF: 335.82853527810573
Iteration:      9,   Func. Count:     59,   Neg. LLF: 303.29215251077636
Iteration:     10,   Func. Count:     64,   Neg. LLF: 432.00177911957746
Iteration:     11,   Func. Count:     71,   Neg. LLF: 1431.908188558945
Iteration:     12,   Func. Count:     78,   Neg. LLF: 303.0386420641224
Iteration:     13,   Func. Count:     83,   Neg. LLF: 303.06452960274726
Iteration:     14,   Func. Count:     89,   Neg. LLF: 30

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [31]:
#SES
ses_errors = []
ses_preds1 = []
#Holt
holt_errors = []
holt_preds1 = []
#Holt-Winter
hw_errors = []
hw_preds1 = []

for i in range(silver_forecasting_horizon) :
    ses_model = SimpleExpSmoothing(silver['y'][:-silver_forecasting_horizon+i])
    ses_model_fit = ses_model.fit()
    ses_pred = ses_model_fit.forecast(1).to_numpy().item()
    ses_error = ses_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    ses_abs_error = abs(ses_error)
    ses_preds1.append(ses_pred)
    ses_errors.append(ses_abs_error)
    
    holt_model = Holt(silver['y'][:-silver_forecasting_horizon+i])
    holt_model_fit = holt_model.fit()
    holt_pred = holt_model_fit.forecast(1).to_numpy().item()
    holt_error = holt_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    holt_abs_error = abs(holt_error)
    holt_preds1.append(holt_pred)
    holt_errors.append(holt_abs_error)
    
    hw_model = ExponentialSmoothing(silver['y'][:-silver_forecasting_horizon+i], seasonal_periods=5, trend='add', seasonal='add')
    hw_model_fit = hw_model.fit()
    hw_pred = hw_model_fit.forecast(1).to_numpy().item()
    hw_error = hw_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    hw_abs_error = abs(hw_error)
    hw_preds1.append(hw_pred)
    hw_errors.append(hw_abs_error)
    
ses_abs_errors = np.array(ses_errors)
ses = ses_abs_errors.mean()
holt_abs_errors = np.array(holt_errors)
holt = holt_abs_errors.mean()
hw_abs_errors = np.array(hw_errors)
hw = hw_abs_errors.mean()

results['Simple Exponential Smoothing'].iloc[3] = ses
results['Holt\'s Exponential Smoothing'].iloc[3] = holt
results['Holt-Winter\'s Exponential Smoothing'].iloc[3] = hw

In [32]:
#prophet
prophet_errors = []
prophet_preds1 = []
#prophet-ARIMA
prophet_arima_errors = []
prophet_arima_preds1 = []

for i in range(silver_forecasting_horizon) :
    date = silver['ds'].iloc[silver.shape[0]-silver_forecasting_horizon+i] - silver['ds'].iloc[silver.shape[0]-silver_forecasting_horizon+i-1]
    m = Prophet()
    m.fit(silver.iloc[:silver.shape[0]-silver_forecasting_horizon+i])
    future = m.make_future_dataframe(periods=date.days)
    forecast = m.predict(future)
    prophet_pred = forecast['yhat'].iloc[-1]
    prophet_error = prophet_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    prophet_abs_error = abs(prophet_error)
    prophet_preds1.append(prophet_pred)
    prophet_errors.append(prophet_abs_error)
    
    
    error_series = silver['y'][:silver.shape[0]-silver_forecasting_horizon+i] - forecast['yhat'].iloc[:-date.days]
    prophet_arima_model = pm.auto_arima(error_series, start_p = 0, start_q = 0, max_p = 5, max_q = 5, \
                                        seasonal = False, information_criteria = 'bic')
    prophet_arima_pred = prophet_arima_model.predict(n_periods=1).to_numpy().item() + prophet_pred
    prophet_arima_error = prophet_arima_pred- silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    prophet_arima_abs_error = abs(prophet_arima_error)
    prophet_arima_preds1.append(prophet_arima_pred)
    prophet_arima_errors.append(prophet_arima_abs_error)    

    
prophet_abs_errors = np.array(prophet_errors)
prophet = prophet_abs_errors.mean()
prophet_arima_abs_errors = np.array(prophet_arima_errors)
prophet_arima = prophet_arima_abs_errors.mean()

results['Prophet'].iloc[3] = prophet
results['Prophet+ARIMA'].iloc[3] = prophet_arima

20:32:57 - cmdstanpy - INFO - Chain [1] start processing
20:32:58 - cmdstanpy - INFO - Chain [1] done processing
20:33:01 - cmdstanpy - INFO - Chain [1] start processing
20:33:01 - cmdstanpy - INFO - Chain [1] done processing
20:33:04 - cmdstanpy - INFO - Chain [1] start processing
20:33:04 - cmdstanpy - INFO - Chain [1] done processing
20:33:07 - cmdstanpy - INFO - Chain [1] start processing
20:33:07 - cmdstanpy - INFO - Chain [1] done processing
20:33:10 - cmdstanpy - INFO - Chain [1] start processing
20:33:10 - cmdstanpy - INFO - Chain [1] done processing
20:33:12 - cmdstanpy - INFO - Chain [1] start processing
20:33:13 - cmdstanpy - INFO - Chain [1] done processing
20:33:15 - cmdstanpy - INFO - Chain [1] start processing
20:33:16 - cmdstanpy - INFO - Chain [1] done processing
20:33:18 - cmdstanpy - INFO - Chain [1] start processing
20:33:18 - cmdstanpy - INFO - Chain [1] done processing
20:33:21 - cmdstanpy - INFO - Chain [1] start processing
20:33:21 - cmdstanpy - INFO - Chain [1]

20:36:27 - cmdstanpy - INFO - Chain [1] done processing
20:36:30 - cmdstanpy - INFO - Chain [1] start processing
20:36:31 - cmdstanpy - INFO - Chain [1] done processing
20:36:33 - cmdstanpy - INFO - Chain [1] start processing
20:36:33 - cmdstanpy - INFO - Chain [1] done processing
20:36:36 - cmdstanpy - INFO - Chain [1] start processing
20:36:36 - cmdstanpy - INFO - Chain [1] done processing
20:36:38 - cmdstanpy - INFO - Chain [1] start processing
20:36:39 - cmdstanpy - INFO - Chain [1] done processing
20:36:41 - cmdstanpy - INFO - Chain [1] start processing
20:36:42 - cmdstanpy - INFO - Chain [1] done processing
20:36:45 - cmdstanpy - INFO - Chain [1] start processing
20:36:45 - cmdstanpy - INFO - Chain [1] done processing
20:36:48 - cmdstanpy - INFO - Chain [1] start processing
20:36:48 - cmdstanpy - INFO - Chain [1] done processing
20:36:51 - cmdstanpy - INFO - Chain [1] start processing
20:36:52 - cmdstanpy - INFO - Chain [1] done processing
20:36:54 - cmdstanpy - INFO - Chain [1] 

In [33]:
silver_pred =pd.DataFrame(index= silver['ds'][-silver_forecasting_horizon:], columns=columns)
silver_pred['Actual'] = list(silver['y'][silver.shape[0]-silver_forecasting_horizon:])
silver_pred['ARIMA'] = arima_preds1
silver_pred['ARIMA-GARCH'] = arch_preds1
silver_pred['ARIMA 2'] = arima_preds2_1
silver_pred['ARIMA-GARCH 2'] = arch_preds2_1
silver_pred['ARIMA 3'] = arima_preds3_1
silver_pred['ARIMA-GARCH 3'] = arch_preds3_1
silver_pred['Simple Exponential Smoothing'] = ses_preds1
silver_pred['Holt\'s Exponential Smoothing'] = holt_preds1
silver_pred['Holt-Winter\'s Exponential Smoothing'] = hw_preds1
silver_pred['Prophet'] = prophet_preds1
silver_pred['Prophet+ARIMA'] = prophet_arima_preds1
silver_pred.to_csv('./results/silver_1step_forecasting.csv')

In [34]:
results.to_csv('./results/mae.csv')

### Silver (5 step)

In [35]:
#ARIMA(1,1,0)
arima_errors = []
arima_preds5 = []
#ARIMA(1,1,0)-GARCH(1,1)
arch_errors = []
arch_preds5 = []
order = (1,1,0)


for i in range(silver_forecasting_horizon) :
    arima_model = ARIMA(silver['y'][:silver.shape[0]-silver_forecasting_horizon-4+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=5).iloc[-1].item()
    arima_error = arima_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds5.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=5).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=5)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds5.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA'].iloc[4] = arima
results['ARIMA-GARCH'].iloc[4] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 2526823608.954928
Iteration:      2,   Func. Count:     17,   Neg. LLF: 1790843.738514732
Iteration:      3,   Func. Count:     24,   Neg. LLF: 306.65517687709945
Iteration:      4,   Func. Count:     30,   Neg. LLF: 278.8433019109399
Iteration:      5,   Func. Count:     36,   Neg. LLF: 275.154687791932
Iteration:      6,   Func. Count:     42,   Neg. LLF: 274.2987314066864
Iteration:      7,   Func. Count:     48,   Neg. LLF: 275.28253268957724
Iteration:      8,   Func. Count:     54,   Neg. LLF: 240.87331882255486
Iteration:      9,   Func. Count:     59,   Neg. LLF: 240.83935696254508
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2563.2308701524603
Iteration:     11,   Func. Count:     72,   Neg. LLF: 2676.218415049107
Iteration:     12,   Func. Count:     79,   Neg. LLF: 239.58181772484437
Iteration:     13,   Func. Count:     84,   Neg. LLF: 239.57817207962592
Iteration:     14,   Func. Count:     89,   Neg. LLF: 239.

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:     13,   Func. Count:     84,   Neg. LLF: 240.13402684702243
Iteration:     14,   Func. Count:     89,   Neg. LLF: 240.1340269874253
Iteration:     15,   Func. Count:     94,   Neg. LLF: 240.13402476009173
Optimization terminated successfully    (Exit mode 0)
            Current function value: 240.13402475878664
            Iterations: 15
            Function evaluations: 94
            Gradient evaluations: 15
Iteration:      1,   Func. Count:      6,   Neg. LLF: 1813071357237054.5
Iteration:      2,   Func. Count:     17,   Neg. LLF: 858361.6811515315
Iteration:      3,   Func. Count:     24,   Neg. LLF: 307.5860511328376
Iteration:      4,   Func. Count:     30,   Neg. LLF: 279.62180596203575
Iteration:      5,   Func. Count:     36,   Neg. LLF: 276.0276141408006
Iteration:      6,   Func. Count:     42,   Neg. LLF: 275.23047007638843
Iteration:      7,   Func. Count:     48,   Neg. LLF: 276.0874611999226
Iteration:      8,   Func. Count:     54,   Neg. LLF: 242.0617016

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      6,   Func. Count:     42,   Neg. LLF: 275.52802239040915
Iteration:      7,   Func. Count:     48,   Neg. LLF: 276.3912114900254
Iteration:      8,   Func. Count:     54,   Neg. LLF: 242.4135344657679
Iteration:      9,   Func. Count:     60,   Neg. LLF: 241.71657460450058
Iteration:     10,   Func. Count:     66,   Neg. LLF: 241.26610243725597
Iteration:     11,   Func. Count:     72,   Neg. LLF: 242.81962228054186
Iteration:     12,   Func. Count:     79,   Neg. LLF: 240.78888647394987
Iteration:     13,   Func. Count:     85,   Neg. LLF: 240.78359958156753
Iteration:     14,   Func. Count:     90,   Neg. LLF: 240.78359521553898
Iteration:     15,   Func. Count:     94,   Neg. LLF: 240.7835952155566
Optimization terminated successfully    (Exit mode 0)
            Current function value: 240.78359521553898
            Iterations: 15
            Function evaluations: 94
            Gradient evaluations: 15
Iteration:      1,   Func. Count:      6,   Neg. LLF: 183657802

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1334946717797976.2
Iteration:      2,   Func. Count:     16,   Neg. LLF: 3475062.855061651
Iteration:      3,   Func. Count:     23,   Neg. LLF: 356.11526174468247
Iteration:      4,   Func. Count:     29,   Neg. LLF: 345.3643730363268
Iteration:      5,   Func. Count:     35,   Neg. LLF: 2958.6607184272825
Iteration:      6,   Func. Count:     42,   Neg. LLF: 340.9661751809857
Iteration:      7,   Func. Count:     48,   Neg. LLF: 340.5577210267928
Iteration:      8,   Func. Count:     54,   Neg. LLF: 334.1048538800177
Iteration:      9,   Func. Count:     60,   Neg. LLF: 305.6586703553303
Iteration:     10,   Func. Count:     65,   Neg. LLF: 305.2495684830618
Iteration:     11,   Func. Count:     70,   Neg. LLF: 3084.1313429205575
Iteration:     12,   Func. Count:     77,   Neg. LLF: 564.2652371010074
Iteration:     13,   Func. Count:     84,   Neg. LLF: 304.9208041728955
Iteration:     14,   Func. Count:     89,   Neg. LLF: 304.91

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1898162376.705476
Iteration:      2,   Func. Count:     16,   Neg. LLF: 686084819.7204133
Iteration:      3,   Func. Count:     23,   Neg. LLF: 358.20378459949825
Iteration:      4,   Func. Count:     29,   Neg. LLF: 346.19651478251717
Iteration:      5,   Func. Count:     35,   Neg. LLF: 354.54204133427663
Iteration:      6,   Func. Count:     41,   Neg. LLF: 341.0047927397791
Iteration:      7,   Func. Count:     47,   Neg. LLF: 548.5649453194733
Iteration:      8,   Func. Count:     53,   Neg. LLF: 310.30561837492684
Iteration:      9,   Func. Count:     59,   Neg. LLF: 305.7047869201364
Iteration:     10,   Func. Count:     65,   Neg. LLF: 11786.98982328044
Iteration:     11,   Func. Count:     72,   Neg. LLF: 306.3248800605858
Iteration:     12,   Func. Count:     78,   Neg. LLF: 305.4170767284595
Iteration:     13,   Func. Count:     84,   Neg. LLF: 305.384680505253
Iteration:     14,   Func. Count:     90,   Neg. LLF: 305.381

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [36]:
#ARIMA(2,1,2)
arima_errors = []
arima_preds2_5 = []
#ARIMA(2,1,2)-GARCH(1,1)
arch_errors = []
arch_preds2_5 = []
order = (2,1,2)


for i in range(silver_forecasting_horizon) :
    arima_model = ARIMA(silver['y'][:silver.shape[0]-silver_forecasting_horizon-4+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=5).iloc[-1].item()
    arima_error = arima_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds2_5.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=5).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=5)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds2_5.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 2'].iloc[4] = arima
results['ARIMA-GARCH 2'].iloc[4] = arch

C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1838806727207958.2
Iteration:      2,   Func. Count:     17,   Neg. LLF: 619881934.4261389
Iteration:      3,   Func. Count:     24,   Neg. LLF: 302.3340700690384
Iteration:      4,   Func. Count:     30,   Neg. LLF: 272.5222371727071
Iteration:      5,   Func. Count:     36,   Neg. LLF: 269.5335330698083
Iteration:      6,   Func. Count:     42,   Neg. LLF: 269.1654157586087
Iteration:      7,   Func. Count:     48,   Neg. LLF: 272.1515364652048
Iteration:      8,   Func. Count:     54,   Neg. LLF: 235.74978945223515
Iteration:      9,   Func. Count:     59,   Neg. LLF: 236.0655744584007
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2587.806661587241
Iteration:     11,   Func. Count:     72,   Neg. LLF: 1959.4957418071967
Iteration:     12,   Func. Count:     79,   Neg. LLF: 234.46497463738487
Iteration:     13,   Func. Count:     84,   Neg. LLF: 234.4626943887434
Iteration:     14,   Func. Count:     89,   Neg. LLF: 234.46

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1861679877664582.8
Iteration:      2,   Func. Count:     17,   Neg. LLF: 619819964.698035
Iteration:      3,   Func. Count:     24,   Neg. LLF: 303.6327836769743
Iteration:      4,   Func. Count:     30,   Neg. LLF: 273.0396861708625
Iteration:      5,   Func. Count:     36,   Neg. LLF: 270.0705500864624
Iteration:      6,   Func. Count:     42,   Neg. LLF: 269.7389647378293
Iteration:      7,   Func. Count:     48,   Neg. LLF: 272.36965572968137
Iteration:      8,   Func. Count:     54,   Neg. LLF: 236.52158208940085
Iteration:      9,   Func. Count:     60,   Neg. LLF: 236.26576962351737
Iteration:     10,   Func. Count:     66,   Neg. LLF: 235.55030494834043
Iteration:     11,   Func. Count:     72,   Neg. LLF: 235.42821949301526
Iteration:     12,   Func. Count:     78,   Neg. LLF: 235.0071795316939
Iteration:     13,   Func. Count:     83,   Neg. LLF: 235.00782538225852
Iteration:     14,   Func. Count:     89,   Neg. LLF: 235.

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 597502385.4523703
Iteration:      2,   Func. Count:     16,   Neg. LLF: 3059716.118782866
Iteration:      3,   Func. Count:     23,   Neg. LLF: 368.0343209390535
Iteration:      4,   Func. Count:     29,   Neg. LLF: 346.3010063544831
Iteration:      5,   Func. Count:     35,   Neg. LLF: 335.9794844186639
Iteration:      6,   Func. Count:     41,   Neg. LLF: 338.67997809370945
Iteration:      7,   Func. Count:     47,   Neg. LLF: 337.0705085480967
Iteration:      8,   Func. Count:     53,   Neg. LLF: 354.9207763921843
Iteration:      9,   Func. Count:     59,   Neg. LLF: 304.04514654356
Iteration:     10,   Func. Count:     65,   Neg. LLF: 302.62867892902676
Iteration:     11,   Func. Count:     71,   Neg. LLF: 474.07967804588685
Iteration:     12,   Func. Count:     78,   Neg. LLF: 302.3247372341931
Iteration:     13,   Func. Count:     84,   Neg. LLF: 302.2578449825139
Iteration:     14,   Func. Count:     89,   Neg. LLF: 302.25782

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 642957438.001541
Iteration:      2,   Func. Count:     16,   Neg. LLF: 3308330.796175183
Iteration:      3,   Func. Count:     23,   Neg. LLF: 369.9701845556719
Iteration:      4,   Func. Count:     29,   Neg. LLF: 346.50629190308985
Iteration:      5,   Func. Count:     35,   Neg. LLF: 335.9836677669259
Iteration:      6,   Func. Count:     41,   Neg. LLF: 336.95647505040705
Iteration:      7,   Func. Count:     47,   Neg. LLF: 896.4632064600753
Iteration:      8,   Func. Count:     53,   Neg. LLF: 336.27625536554706
Iteration:      9,   Func. Count:     59,   Neg. LLF: 302.5159909052465
Iteration:     10,   Func. Count:     64,   Neg. LLF: 425.4008875959706
Iteration:     11,   Func. Count:     71,   Neg. LLF: 1310.0060787509888
Iteration:     12,   Func. Count:     78,   Neg. LLF: 302.3489137437127
Iteration:     13,   Func. Count:     84,   Neg. LLF: 302.33865541810746
Iteration:     14,   Func. Count:     89,   Neg. LLF: 302.33

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [37]:
#ARIMA(0,1,4)
arima_errors = []
arima_preds3_5 = []
#ARIMA(0,1,4)-GARCH(1,1)
arch_errors = []
arch_preds3_5 = []
order = (0,1,4)


for i in range(silver_forecasting_horizon) :
    arima_model = ARIMA(silver['y'][:silver.shape[0]-silver_forecasting_horizon-4+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=5).iloc[-1].item()
    arima_error = arima_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds3_5.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=5).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=5)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds3_5.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 3'].iloc[4] = arima
results['ARIMA-GARCH 3'].iloc[4] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 2111032751.9171603
Iteration:      2,   Func. Count:     17,   Neg. LLF: 618869237.7120476
Iteration:      3,   Func. Count:     24,   Neg. LLF: 301.75430023744065
Iteration:      4,   Func. Count:     30,   Neg. LLF: 271.527344640858
Iteration:      5,   Func. Count:     36,   Neg. LLF: 268.77103788884114
Iteration:      6,   Func. Count:     42,   Neg. LLF: 268.2176940646228
Iteration:      7,   Func. Count:     48,   Neg. LLF: 271.8782237032128
Iteration:      8,   Func. Count:     54,   Neg. LLF: 235.71693838774638
Iteration:      9,   Func. Count:     59,   Neg. LLF: 236.17972662719302
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2411.1805199815267
Iteration:     11,   Func. Count:     72,   Neg. LLF: 1752.161135853626
Iteration:     12,   Func. Count:     79,   Neg. LLF: 234.59733574371597
Iteration:     13,   Func. Count:     84,   Neg. LLF: 234.5962284179954
Iteration:     14,   Func. Count:     89,   Neg. LLF: 234.

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1937617868732098.2
Iteration:      2,   Func. Count:     17,   Neg. LLF: 618881276.1123172
Iteration:      3,   Func. Count:     24,   Neg. LLF: 301.8643817064263
Iteration:      4,   Func. Count:     30,   Neg. LLF: 271.75335835851575
Iteration:      5,   Func. Count:     36,   Neg. LLF: 269.025200006771
Iteration:      6,   Func. Count:     42,   Neg. LLF: 268.4657552790645
Iteration:      7,   Func. Count:     48,   Neg. LLF: 272.10954241034676
Iteration:      8,   Func. Count:     54,   Neg. LLF: 236.1351361885353
Iteration:      9,   Func. Count:     59,   Neg. LLF: 236.5314437098375
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2427.039730699521
Iteration:     11,   Func. Count:     72,   Neg. LLF: 1761.8886579604082
Iteration:     12,   Func. Count:     79,   Neg. LLF: 234.88356016998398
Iteration:     13,   Func. Count:     84,   Neg. LLF: 234.8823877008851
Iteration:     14,   Func. Count:     89,   Neg. LLF: 234.88

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1955263578363789.2
Iteration:      2,   Func. Count:     17,   Neg. LLF: 333640.2075777366
Iteration:      3,   Func. Count:     24,   Neg. LLF: 302.1160379915043
Iteration:      4,   Func. Count:     30,   Neg. LLF: 272.0621548531011
Iteration:      5,   Func. Count:     36,   Neg. LLF: 269.3042951269376
Iteration:      6,   Func. Count:     42,   Neg. LLF: 268.74646817922235
Iteration:      7,   Func. Count:     48,   Neg. LLF: 272.2601756477011
Iteration:      8,   Func. Count:     54,   Neg. LLF: 236.5453307382426
Iteration:      9,   Func. Count:     60,   Neg. LLF: 236.4105203694853
Iteration:     10,   Func. Count:     66,   Neg. LLF: 235.53953586250947
Iteration:     11,   Func. Count:     72,   Neg. LLF: 244.5334816090032
Iteration:     12,   Func. Count:     79,   Neg. LLF: 235.12767558370473
Iteration:     13,   Func. Count:     84,   Neg. LLF: 235.12833613846269
Iteration:     14,   Func. Count:     90,   Neg. LLF: 235.1

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1447399497915272.5
Iteration:      2,   Func. Count:     16,   Neg. LLF: 683808760.1459591
Iteration:      3,   Func. Count:     23,   Neg. LLF: 369.722834377462
Iteration:      4,   Func. Count:     29,   Neg. LLF: 346.3245544777528
Iteration:      5,   Func. Count:     35,   Neg. LLF: 335.6378771095571
Iteration:      6,   Func. Count:     41,   Neg. LLF: 340.1888904188378
Iteration:      7,   Func. Count:     47,   Neg. LLF: 337.3631124405175
Iteration:      8,   Func. Count:     53,   Neg. LLF: 540.1315276954692
Iteration:      9,   Func. Count:     59,   Neg. LLF: 303.1679375528781
Iteration:     10,   Func. Count:     64,   Neg. LLF: 435.6912422577736
Iteration:     11,   Func. Count:     71,   Neg. LLF: 1340.0855987590248
Iteration:     12,   Func. Count:     78,   Neg. LLF: 303.0500712052064
Iteration:     13,   Func. Count:     84,   Neg. LLF: 303.0462421361656
Iteration:     14,   Func. Count:     89,   Neg. LLF: 303.04608

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1593002798.5538583
Iteration:      2,   Func. Count:     16,   Neg. LLF: 2346212.31657382
Iteration:      3,   Func. Count:     23,   Neg. LLF: 372.5797662480686
Iteration:      4,   Func. Count:     29,   Neg. LLF: 346.79001484482876
Iteration:      5,   Func. Count:     35,   Neg. LLF: 336.4985859627326
Iteration:      6,   Func. Count:     41,   Neg. LLF: 450.1363061503316
Iteration:      7,   Func. Count:     47,   Neg. LLF: 335.58710348916475
Iteration:      8,   Func. Count:     53,   Neg. LLF: 304.3749880717132
Iteration:      9,   Func. Count:     59,   Neg. LLF: 303.3993988747555
Iteration:     10,   Func. Count:     65,   Neg. LLF: 400.7210791374315
Iteration:     11,   Func. Count:     72,   Neg. LLF: 303.64165933870424
Iteration:     12,   Func. Count:     78,   Neg. LLF: 303.1321145786157
Iteration:     13,   Func. Count:     84,   Neg. LLF: 303.1301150765123
Iteration:     14,   Func. Count:     89,   Neg. LLF: 303.130

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [38]:
#SES
ses_errors = []
ses_preds5= []
#Holt
holt_errors = []
holt_preds5= []
#Holt-Winter
hw_errors = []
hw_preds5= []

for i in range(silver_forecasting_horizon) :
    ses_model = SimpleExpSmoothing(silver['y'][:-silver_forecasting_horizon-4+i])
    ses_model_fit = ses_model.fit()
    ses_pred = ses_model_fit.forecast(5).iloc[-1].item()
    ses_error = ses_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    ses_abs_error = abs(ses_error)
    ses_preds5.append(ses_pred)
    ses_errors.append(ses_abs_error)
    
    holt_model = Holt(silver['y'][:-silver_forecasting_horizon-4+i])
    holt_model_fit = holt_model.fit()
    holt_pred = holt_model_fit.forecast(5).iloc[-1].item()
    holt_error = holt_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    holt_abs_error = abs(holt_error)
    holt_preds5.append(holt_pred)
    holt_errors.append(holt_abs_error)
    
    hw_model = ExponentialSmoothing(silver['y'][:-silver_forecasting_horizon-4+i], seasonal_periods=5, trend='add', seasonal='add')
    hw_model_fit = hw_model.fit()
    hw_pred = hw_model_fit.forecast(5).iloc[-1].item()
    hw_error = hw_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    hw_abs_error = abs(hw_error)
    hw_preds5.append(hw_pred)
    hw_errors.append(hw_abs_error)
    
ses_abs_errors = np.array(ses_errors)
ses = ses_abs_errors.mean()
holt_abs_errors = np.array(holt_errors)
holt = holt_abs_errors.mean()
hw_abs_errors = np.array(hw_errors)
hw = hw_abs_errors.mean()

results['Simple Exponential Smoothing'].iloc[4] = ses
results['Holt\'s Exponential Smoothing'].iloc[4] = holt
results['Holt-Winter\'s Exponential Smoothing'].iloc[4] = hw

In [39]:
#prophet
prophet_errors = []
prophet_preds5 = []
#prophet-ARIMA
prophet_arima_errors = []
prophet_arima_preds5 = []

for i in range(silver_forecasting_horizon) :
    date = silver['ds'].iloc[silver.shape[0]-silver_forecasting_horizon+i] - silver['ds'].iloc[silver.shape[0]-silver_forecasting_horizon-5+i]
    m = Prophet()
    m.fit(silver.iloc[:silver.shape[0]-silver_forecasting_horizon-4+i])
    future = m.make_future_dataframe(periods=date.days)
    forecast = m.predict(future)
    prophet_pred = forecast['yhat'].iloc[-1]
    prophet_error = prophet_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    prophet_abs_error = abs(prophet_error)
    prophet_preds5.append(prophet_pred)
    prophet_errors.append(prophet_abs_error)
    
    
    error_series = silver['y'][:silver.shape[0]-silver_forecasting_horizon-4+i] - forecast['yhat'].iloc[:-date.days]
    prophet_arima_model = pm.auto_arima(error_series, start_p = 0, start_q = 0, max_p = 5, max_q = 5, \
                                        seasonal = False, information_criteria = 'bic')
    prophet_arima_pred = prophet_arima_model.predict(n_periods=5).iloc[-1].item() + prophet_pred
    prophet_arima_error = prophet_arima_pred- silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    prophet_arima_abs_error = abs(prophet_arima_error)
    prophet_arima_preds5.append(prophet_arima_pred)
    prophet_arima_errors.append(prophet_arima_abs_error)    

    
prophet_abs_errors = np.array(prophet_errors)
prophet = prophet_abs_errors.mean()
prophet_arima_abs_errors = np.array(prophet_arima_errors)
prophet_arima = prophet_arima_abs_errors.mean()

results['Prophet'].iloc[4] = prophet
results['Prophet+ARIMA'].iloc[4] = prophet_arima

20:41:53 - cmdstanpy - INFO - Chain [1] start processing
20:41:53 - cmdstanpy - INFO - Chain [1] done processing
20:41:56 - cmdstanpy - INFO - Chain [1] start processing
20:41:56 - cmdstanpy - INFO - Chain [1] done processing
20:41:59 - cmdstanpy - INFO - Chain [1] start processing
20:41:59 - cmdstanpy - INFO - Chain [1] done processing
20:42:02 - cmdstanpy - INFO - Chain [1] start processing
20:42:02 - cmdstanpy - INFO - Chain [1] done processing
20:42:04 - cmdstanpy - INFO - Chain [1] start processing
20:42:05 - cmdstanpy - INFO - Chain [1] done processing
20:42:08 - cmdstanpy - INFO - Chain [1] start processing
20:42:08 - cmdstanpy - INFO - Chain [1] done processing
20:42:10 - cmdstanpy - INFO - Chain [1] start processing
20:42:11 - cmdstanpy - INFO - Chain [1] done processing
20:42:13 - cmdstanpy - INFO - Chain [1] start processing
20:42:14 - cmdstanpy - INFO - Chain [1] done processing
20:42:16 - cmdstanpy - INFO - Chain [1] start processing
20:42:17 - cmdstanpy - INFO - Chain [1]

20:45:24 - cmdstanpy - INFO - Chain [1] done processing
20:45:26 - cmdstanpy - INFO - Chain [1] start processing
20:45:26 - cmdstanpy - INFO - Chain [1] done processing
20:45:29 - cmdstanpy - INFO - Chain [1] start processing
20:45:29 - cmdstanpy - INFO - Chain [1] done processing
20:45:32 - cmdstanpy - INFO - Chain [1] start processing
20:45:32 - cmdstanpy - INFO - Chain [1] done processing
20:45:35 - cmdstanpy - INFO - Chain [1] start processing
20:45:35 - cmdstanpy - INFO - Chain [1] done processing
20:45:38 - cmdstanpy - INFO - Chain [1] start processing
20:45:39 - cmdstanpy - INFO - Chain [1] done processing
20:45:41 - cmdstanpy - INFO - Chain [1] start processing
20:45:42 - cmdstanpy - INFO - Chain [1] done processing
20:45:44 - cmdstanpy - INFO - Chain [1] start processing
20:45:44 - cmdstanpy - INFO - Chain [1] done processing
20:45:47 - cmdstanpy - INFO - Chain [1] start processing
20:45:48 - cmdstanpy - INFO - Chain [1] done processing
20:45:50 - cmdstanpy - INFO - Chain [1] 

In [40]:
silver_pred =pd.DataFrame(index= silver['ds'][-silver_forecasting_horizon:], columns=columns)
silver_pred['Actual'] = list(silver['y'][silver.shape[0]-silver_forecasting_horizon:])
silver_pred['ARIMA'] = arima_preds5
silver_pred['ARIMA-GARCH'] = arch_preds5
silver_pred['ARIMA 2'] = arima_preds2_5
silver_pred['ARIMA-GARCH 2'] = arch_preds2_5
silver_pred['ARIMA 3'] = arima_preds3_5
silver_pred['ARIMA-GARCH 3'] = arch_preds3_5
silver_pred['Simple Exponential Smoothing'] = ses_preds5
silver_pred['Holt\'s Exponential Smoothing'] = holt_preds5
silver_pred['Holt-Winter\'s Exponential Smoothing'] = hw_preds5
silver_pred['Prophet'] = prophet_preds5
silver_pred['Prophet+ARIMA'] = prophet_arima_preds5
silver_pred.to_csv('./results/silver_5step_forecasting.csv')

In [41]:
results.to_csv('./results/mae.csv')

### Silver (10 step)

In [42]:
#ARIMA(1,1,0)
arima_errors = []
arima_preds10 = []
#ARIMA(1,1,0)-GARCH(1,1)
arch_errors = []
arch_preds10 = []
order = (1,1,0)


for i in range(silver_forecasting_horizon) :
    arima_model = ARIMA(silver['y'][:silver.shape[0]-silver_forecasting_horizon-9+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=10).iloc[-1].item()
    arima_error = arima_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds10.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=10).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=10)
    predicted_et = garch_forecast.mean['h.01'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds10.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA'].iloc[5] = arima
results['ARIMA-GARCH'].iloc[5] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 1329083630.6973453
Iteration:      2,   Func. Count:     17,   Neg. LLF: 488502.37328324094
Iteration:      3,   Func. Count:     24,   Neg. LLF: 304.89758191065056
Iteration:      4,   Func. Count:     30,   Neg. LLF: 276.9094159033644
Iteration:      5,   Func. Count:     36,   Neg. LLF: 272.6966440736917
Iteration:      6,   Func. Count:     42,   Neg. LLF: 272.22958129197116
Iteration:      7,   Func. Count:     48,   Neg. LLF: 273.5163408494314
Iteration:      8,   Func. Count:     54,   Neg. LLF: 237.91611266729748
Iteration:      9,   Func. Count:     59,   Neg. LLF: 238.03784832779354
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2857.9139428619465
Iteration:     11,   Func. Count:     72,   Neg. LLF: 237.05719059067982
Iteration:     12,   Func. Count:     78,   Neg. LLF: 238.92446407241948
Iteration:     13,   Func. Count:     84,   Neg. LLF: 236.88796881083238
Iteration:     14,   Func. Count:     89,   Neg. LLF: 

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      6,   Func. Count:     42,   Neg. LLF: 273.07931445789774
Iteration:      7,   Func. Count:     48,   Neg. LLF: 274.3556231508999
Iteration:      8,   Func. Count:     54,   Neg. LLF: 239.2105989608322
Iteration:      9,   Func. Count:     59,   Neg. LLF: 239.29122482551108
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2609.3672965392043
Iteration:     11,   Func. Count:     72,   Neg. LLF: 394.21214826450796
Iteration:     12,   Func. Count:     80,   Neg. LLF: 238.1250738052091
Iteration:     13,   Func. Count:     85,   Neg. LLF: 238.12177257476836
Iteration:     14,   Func. Count:     90,   Neg. LLF: 238.12176557905065
Iteration:     15,   Func. Count:     94,   Neg. LLF: 238.12176557921737
Optimization terminated successfully    (Exit mode 0)
            Current function value: 238.12176557905065
            Iterations: 15
            Function evaluations: 94
            Gradient evaluations: 15
Iteration:      1,   Func. Count:      6,   Neg. LLF: 369259650

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 2526823608.954928
Iteration:      2,   Func. Count:     17,   Neg. LLF: 1790843.738514732
Iteration:      3,   Func. Count:     24,   Neg. LLF: 306.65517687709945
Iteration:      4,   Func. Count:     30,   Neg. LLF: 278.8433019109399
Iteration:      5,   Func. Count:     36,   Neg. LLF: 275.154687791932
Iteration:      6,   Func. Count:     42,   Neg. LLF: 274.2987314066864
Iteration:      7,   Func. Count:     48,   Neg. LLF: 275.28253268957724
Iteration:      8,   Func. Count:     54,   Neg. LLF: 240.87331882255486
Iteration:      9,   Func. Count:     59,   Neg. LLF: 240.83935696254508
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2563.2308701524603
Iteration:     11,   Func. Count:     72,   Neg. LLF: 2676.218415049107
Iteration:     12,   Func. Count:     79,   Neg. LLF: 239.58181772484437
Iteration:     13,   Func. Count:     84,   Neg. LLF: 239.57817207962592
Iteration:     14,   Func. Count:     89,   Neg. LLF: 239.

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 21933015391.97796
Iteration:      2,   Func. Count:     16,   Neg. LLF: 680357299.0013783
Iteration:      3,   Func. Count:     23,   Neg. LLF: 355.70803687935336
Iteration:      4,   Func. Count:     29,   Neg. LLF: 341.78355806576536
Iteration:      5,   Func. Count:     35,   Neg. LLF: 337.98047550756974
Iteration:      6,   Func. Count:     41,   Neg. LLF: 334.21550684364917
Iteration:      7,   Func. Count:     47,   Neg. LLF: 2974.600509632688
Iteration:      8,   Func. Count:     53,   Neg. LLF: 333.8199335010349
Iteration:      9,   Func. Count:     59,   Neg. LLF: 300.09586297973794
Iteration:     10,   Func. Count:     64,   Neg. LLF: 512537082.1866248
Iteration:     11,   Func. Count:     71,   Neg. LLF: 1068.4733181005288
Iteration:     12,   Func. Count:     78,   Neg. LLF: 299.8746441844047
Iteration:     13,   Func. Count:     83,   Neg. LLF: 299.8421901775487
Iteration:     14,   Func. Count:     88,   Neg. LLF: 299.

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 1344092800741497.0
Iteration:      2,   Func. Count:     16,   Neg. LLF: 685196282.4166464
Iteration:      3,   Func. Count:     23,   Neg. LLF: 356.46803910300684
Iteration:      4,   Func. Count:     29,   Neg. LLF: 345.31365142241737
Iteration:      5,   Func. Count:     35,   Neg. LLF: 459.5785418414272
Iteration:      6,   Func. Count:     41,   Neg. LLF: 340.7138465872897
Iteration:      7,   Func. Count:     47,   Neg. LLF: 363.8683260294338
Iteration:      8,   Func. Count:     53,   Neg. LLF: 339.80829049866895
Iteration:      9,   Func. Count:     59,   Neg. LLF: 304.68805207641014
Iteration:     10,   Func. Count:     64,   Neg. LLF: 12680.31338397282
Iteration:     11,   Func. Count:     71,   Neg. LLF: 1126.1005907716758
Iteration:     12,   Func. Count:     79,   Neg. LLF: 304.5328535307252
Iteration:     13,   Func. Count:     84,   Neg. LLF: 304.53285281492333
Optimization terminated successfully    (Exit mode 0)
   

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [43]:
#ARIMA(2,1,2)
arima_errors = []
arima_preds2_10 = []
#ARIMA(2,1,2)-GARCH(1,1)
arch_errors = []
arch_preds2_10 = []
order = (2,1,2)


for i in range(silver_forecasting_horizon) :
    arima_model = ARIMA(silver['y'][:silver.shape[0]-silver_forecasting_horizon-9+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=10).iloc[-1].item()
    arima_error = arima_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds2_10.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=10).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=10)
    predicted_et = garch_forecast.mean['h.01'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds2_10.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 2'].iloc[5] = arima
results['ARIMA-GARCH 2'].iloc[5] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 845712851.8722978
Iteration:      2,   Func. Count:     17,   Neg. LLF: 619610320.9231889
Iteration:      3,   Func. Count:     24,   Neg. LLF: 301.42570793236973
Iteration:      4,   Func. Count:     30,   Neg. LLF: 270.6138457458254
Iteration:      5,   Func. Count:     36,   Neg. LLF: 267.4910408644667
Iteration:      6,   Func. Count:     42,   Neg. LLF: 267.50402474469814
Iteration:      7,   Func. Count:     48,   Neg. LLF: 269.6097942901121
Iteration:      8,   Func. Count:     54,   Neg. LLF: 232.69825062069518
Iteration:      9,   Func. Count:     59,   Neg. LLF: 233.24973691685005
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2872.4146432835632
Iteration:     11,   Func. Count:     72,   Neg. LLF: 1682.3889512370226
Iteration:     12,   Func. Count:     80,   Neg. LLF: 231.7859210489775
Iteration:     13,   Func. Count:     85,   Neg. LLF: 231.78008804987496
Iteration:     14,   Func. Count:     90,   Neg. LLF: 231

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 573246728.1493065
Iteration:      2,   Func. Count:     17,   Neg. LLF: 417389.9347660518
Iteration:      3,   Func. Count:     24,   Neg. LLF: 301.579694169258
Iteration:      4,   Func. Count:     30,   Neg. LLF: 271.1171742491073
Iteration:      5,   Func. Count:     36,   Neg. LLF: 267.9703782028755
Iteration:      6,   Func. Count:     42,   Neg. LLF: 267.92727045257885
Iteration:      7,   Func. Count:     48,   Neg. LLF: 270.2370925822861
Iteration:      8,   Func. Count:     54,   Neg. LLF: 233.345111091682
Iteration:      9,   Func. Count:     59,   Neg. LLF: 233.88028267492737
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2855.1713390405544
Iteration:     11,   Func. Count:     72,   Neg. LLF: 1729.1883526448294
Iteration:     12,   Func. Count:     79,   Neg. LLF: 232.43489590468312
Iteration:     13,   Func. Count:     84,   Neg. LLF: 232.4305804390987
Iteration:     14,   Func. Count:     89,   Neg. LLF: 232.430

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 354116161.54251045
Iteration:      2,   Func. Count:     17,   Neg. LLF: 1195499.7769536395
Iteration:      3,   Func. Count:     24,   Neg. LLF: 301.2374671100011
Iteration:      4,   Func. Count:     30,   Neg. LLF: 271.5384311491923
Iteration:      5,   Func. Count:     36,   Neg. LLF: 268.5126967735166
Iteration:      6,   Func. Count:     42,   Neg. LLF: 268.25596413101704
Iteration:      7,   Func. Count:     48,   Neg. LLF: 271.0439812598135
Iteration:      8,   Func. Count:     54,   Neg. LLF: 234.08742872605575
Iteration:      9,   Func. Count:     59,   Neg. LLF: 234.566953195876
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2629.636353958188
Iteration:     11,   Func. Count:     72,   Neg. LLF: 1789.6791870367142
Iteration:     12,   Func. Count:     79,   Neg. LLF: 233.09846324928873
Iteration:     13,   Func. Count:     84,   Neg. LLF: 233.09558671795307
Iteration:     14,   Func. Count:     89,   Neg. LLF: 233.

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 562337784.1135987
Iteration:      2,   Func. Count:     16,   Neg. LLF: 679294025.8403243
Iteration:      3,   Func. Count:     23,   Neg. LLF: 357.53970214016925
Iteration:      4,   Func. Count:     29,   Neg. LLF: 340.3105314392087
Iteration:      5,   Func. Count:     35,   Neg. LLF: 332.30924185605977
Iteration:      6,   Func. Count:     41,   Neg. LLF: 2951.3190668362668
Iteration:      7,   Func. Count:     47,   Neg. LLF: 330.7402947619197
Iteration:      8,   Func. Count:     53,   Neg. LLF: 297.7548203259167
Iteration:      9,   Func. Count:     58,   Neg. LLF: 297.9756114317391
Iteration:     10,   Func. Count:     64,   Neg. LLF: 2110.9713709520993
Iteration:     11,   Func. Count:     71,   Neg. LLF: 1986.8464315313051
Iteration:     12,   Func. Count:     78,   Neg. LLF: 297.2570912170346
Iteration:     13,   Func. Count:     83,   Neg. LLF: 297.25699116345413
Iteration:     14,   Func. Count:     88,   Neg. LLF: 297.

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 1408021068910181.8
Iteration:      2,   Func. Count:     16,   Neg. LLF: 683111058.7738087
Iteration:      3,   Func. Count:     23,   Neg. LLF: 362.2129478529133
Iteration:      4,   Func. Count:     29,   Neg. LLF: 344.61662808914645
Iteration:      5,   Func. Count:     35,   Neg. LLF: 336.6202952009951
Iteration:      6,   Func. Count:     41,   Neg. LLF: 448.4188478837491
Iteration:      7,   Func. Count:     47,   Neg. LLF: 334.8439741576699
Iteration:      8,   Func. Count:     53,   Neg. LLF: 302.1123923803227
Iteration:      9,   Func. Count:     58,   Neg. LLF: 301.72849084632435
Iteration:     10,   Func. Count:     64,   Neg. LLF: 2531.130867953344
Iteration:     11,   Func. Count:     71,   Neg. LLF: 301.84068799339354
Iteration:     12,   Func. Count:     78,   Neg. LLF: 301.21765526947735
Iteration:     13,   Func. Count:     84,   Neg. LLF: 301.03855791676006
Iteration:     14,   Func. Count:     89,   Neg. LLF: 301.

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [44]:
#ARIMA(0,1,4)
arima_errors = []
arima_preds3_10 = []
#ARIMA(0,1,4)-GARCH(1,1)
arch_errors = []
arch_preds3_10 = []
order = (0,1,4)


for i in range(silver_forecasting_horizon) :
    arima_model = ARIMA(silver['y'][:silver.shape[0]-silver_forecasting_horizon-9+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=10).iloc[-1].item()
    arima_error = arima_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds3_10.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=10).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=10)
    predicted_et = garch_forecast.mean['h.01'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds3_10.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 3'].iloc[5] = arima
results['ARIMA-GARCH 3'].iloc[5] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 357861032.72355765
Iteration:      2,   Func. Count:     17,   Neg. LLF: 618592163.7556703
Iteration:      3,   Func. Count:     24,   Neg. LLF: 300.4039671878906
Iteration:      4,   Func. Count:     30,   Neg. LLF: 269.6877269896848
Iteration:      5,   Func. Count:     36,   Neg. LLF: 266.8049997630591
Iteration:      6,   Func. Count:     42,   Neg. LLF: 266.37086414052317
Iteration:      7,   Func. Count:     48,   Neg. LLF: 269.46890184953907
Iteration:      8,   Func. Count:     54,   Neg. LLF: 232.84780999647836
Iteration:      9,   Func. Count:     59,   Neg. LLF: 233.44443537965884
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2340.206324142977
Iteration:     11,   Func. Count:     72,   Neg. LLF: 232.21272324956493
Iteration:     12,   Func. Count:     78,   Neg. LLF: 278.85928091777566
Iteration:     13,   Func. Count:     85,   Neg. LLF: 231.98272407047483
Iteration:     14,   Func. Count:     90,   Neg. LLF: 23

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 612298444.9196808
Iteration:      2,   Func. Count:     17,   Neg. LLF: 1068744.263104786
Iteration:      3,   Func. Count:     24,   Neg. LLF: 300.4906220234191
Iteration:      4,   Func. Count:     30,   Neg. LLF: 270.1041112787818
Iteration:      5,   Func. Count:     36,   Neg. LLF: 267.26656271511115
Iteration:      6,   Func. Count:     42,   Neg. LLF: 266.84753474215466
Iteration:      7,   Func. Count:     48,   Neg. LLF: 270.0079108565223
Iteration:      8,   Func. Count:     54,   Neg. LLF: 233.42869727003296
Iteration:      9,   Func. Count:     59,   Neg. LLF: 234.0541743722407
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2381.854122916918
Iteration:     11,   Func. Count:     72,   Neg. LLF: 232.6859807463263
Iteration:     12,   Func. Count:     78,   Neg. LLF: 233.62354643043912
Iteration:     13,   Func. Count:     84,   Neg. LLF: 232.64160041958615
Iteration:     14,   Func. Count:     90,   Neg. LLF: 232.5

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 411662845.2545608
Iteration:      2,   Func. Count:     17,   Neg. LLF: 1354447.328276084
Iteration:      3,   Func. Count:     24,   Neg. LLF: 300.26772370352097
Iteration:      4,   Func. Count:     30,   Neg. LLF: 270.57246480359606
Iteration:      5,   Func. Count:     36,   Neg. LLF: 267.81468328693353
Iteration:      6,   Func. Count:     42,   Neg. LLF: 267.1852683702025
Iteration:      7,   Func. Count:     48,   Neg. LLF: 270.88806874011516
Iteration:      8,   Func. Count:     54,   Neg. LLF: 234.2013156351993
Iteration:      9,   Func. Count:     59,   Neg. LLF: 234.74075380321023
Iteration:     10,   Func. Count:     65,   Neg. LLF: 2339.2351892033994
Iteration:     11,   Func. Count:     72,   Neg. LLF: 237.38066796158864
Iteration:     12,   Func. Count:     79,   Neg. LLF: 233.85241356217932
Iteration:     13,   Func. Count:     85,   Neg. LLF: 233.29419630410828
Iteration:     14,   Func. Count:     90,   Neg. LLF: 2

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 2197233262.762815
Iteration:      2,   Func. Count:     16,   Neg. LLF: 679013626.1995459
Iteration:      3,   Func. Count:     23,   Neg. LLF: 357.08618769442586
Iteration:      4,   Func. Count:     29,   Neg. LLF: 340.368628777976
Iteration:      5,   Func. Count:     35,   Neg. LLF: 332.31850319743216
Iteration:      6,   Func. Count:     41,   Neg. LLF: 2951.279956701449
Iteration:      7,   Func. Count:     47,   Neg. LLF: 330.69122738146683
Iteration:      8,   Func. Count:     53,   Neg. LLF: 298.72057121697605
Iteration:      9,   Func. Count:     58,   Neg. LLF: 298.9507995704863
Iteration:     10,   Func. Count:     64,   Neg. LLF: 2099.7075853609595
Iteration:     11,   Func. Count:     71,   Neg. LLF: 1987.1848584319414
Iteration:     12,   Func. Count:     78,   Neg. LLF: 298.29777836024107
Iteration:     13,   Func. Count:     83,   Neg. LLF: 298.2976635616621
Iteration:     14,   Func. Count:     88,   Neg. LLF: 298.

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 3788170060.094597
Iteration:      2,   Func. Count:     16,   Neg. LLF: 1518969.870337747
Iteration:      3,   Func. Count:     23,   Neg. LLF: 362.2362826302769
Iteration:      4,   Func. Count:     29,   Neg. LLF: 344.54540655382755
Iteration:      5,   Func. Count:     35,   Neg. LLF: 335.8687396301209
Iteration:      6,   Func. Count:     41,   Neg. LLF: 677.2188255632316
Iteration:      7,   Func. Count:     47,   Neg. LLF: 334.5576896050891
Iteration:      8,   Func. Count:     53,   Neg. LLF: 302.44483768744436
Iteration:      9,   Func. Count:     58,   Neg. LLF: 302.51800590222
Iteration:     10,   Func. Count:     64,   Neg. LLF: 2159.7790800951375
Iteration:     11,   Func. Count:     71,   Neg. LLF: 327.329911340563
Iteration:     12,   Func. Count:     79,   Neg. LLF: 301.8908440532265
Iteration:     13,   Func. Count:     84,   Neg. LLF: 301.8907634213407
Iteration:     14,   Func. Count:     89,   Neg. LLF: 301.890761

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [45]:
#SES
ses_errors = []
ses_preds10 = []
#Holt
holt_errors = []
holt_preds10 = []
#Holt-Winter
hw_errors = []
hw_preds10 = []

for i in range(silver_forecasting_horizon) :
    ses_model = SimpleExpSmoothing(silver['y'][:-silver_forecasting_horizon-9+i])
    ses_model_fit = ses_model.fit()
    ses_pred = ses_model_fit.forecast(10).iloc[-1].item()
    ses_error = ses_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    ses_abs_error = abs(ses_error)
    ses_preds10.append(ses_pred)
    ses_errors.append(ses_abs_error)
    
    holt_model = Holt(silver['y'][:-silver_forecasting_horizon-9+i])
    holt_model_fit = holt_model.fit()
    holt_pred = holt_model_fit.forecast(10).iloc[-1].item()
    holt_error = holt_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    holt_abs_error = abs(holt_error)
    holt_preds10.append(holt_pred)
    holt_errors.append(holt_abs_error)
    
    hw_model = ExponentialSmoothing(silver['y'][:-silver_forecasting_horizon-9+i], seasonal_periods=5, trend='add', seasonal='add')
    hw_model_fit = hw_model.fit()
    hw_pred = hw_model_fit.forecast(10).iloc[-1].item()
    hw_error = hw_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    hw_abs_error = abs(hw_error)
    hw_preds10.append(hw_pred)
    hw_errors.append(hw_abs_error)
    
ses_abs_errors = np.array(ses_errors)
ses = ses_abs_errors.mean()
holt_abs_errors = np.array(holt_errors)
holt = holt_abs_errors.mean()
hw_abs_errors = np.array(hw_errors)
hw = hw_abs_errors.mean()

results['Simple Exponential Smoothing'].iloc[5] = ses
results['Holt\'s Exponential Smoothing'].iloc[5] = holt
results['Holt-Winter\'s Exponential Smoothing'].iloc[5] = hw

In [46]:
#prophet
prophet_errors = []
prophet_preds10 = []
#prophet-ARIMA
prophet_arima_errors = []
prophet_arima_preds10 = []

for i in range(silver_forecasting_horizon) :
    date = silver['ds'].iloc[silver.shape[0]-silver_forecasting_horizon+i] - silver['ds'].iloc[silver.shape[0]-silver_forecasting_horizon-10+i]
    m = Prophet()
    m.fit(silver.iloc[:silver.shape[0]-silver_forecasting_horizon-9+i])
    future = m.make_future_dataframe(periods=date.days)
    forecast = m.predict(future)
    prophet_pred = forecast['yhat'].iloc[-1]
    prophet_error = prophet_pred - silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    prophet_abs_error = abs(prophet_error)
    prophet_preds10.append(prophet_pred)
    prophet_errors.append(prophet_abs_error)
    
    
    error_series = silver['y'][:silver.shape[0]-silver_forecasting_horizon-9+i] - forecast['yhat'].iloc[:-date.days]
    prophet_arima_model = pm.auto_arima(error_series, start_p = 0, start_q = 0, max_p = 5, max_q = 5, \
                                        seasonal = False, information_criteria = 'bic')
    prophet_arima_pred = prophet_arima_model.predict(n_periods=10).iloc[-1].item() + prophet_pred
    prophet_arima_error = prophet_arima_pred- silver['y'][silver.shape[0]-silver_forecasting_horizon+i]
    prophet_arima_abs_error = abs(prophet_arima_error)
    prophet_arima_preds10.append(prophet_arima_pred)
    prophet_arima_errors.append(prophet_arima_abs_error)    

    
prophet_abs_errors = np.array(prophet_errors)
prophet = prophet_abs_errors.mean()
prophet_arima_abs_errors = np.array(prophet_arima_errors)
prophet_arima = prophet_arima_abs_errors.mean()

results['Prophet'].iloc[5] = prophet
results['Prophet+ARIMA'].iloc[5] = prophet_arima

20:50:42 - cmdstanpy - INFO - Chain [1] start processing
20:50:43 - cmdstanpy - INFO - Chain [1] done processing
20:50:45 - cmdstanpy - INFO - Chain [1] start processing
20:50:45 - cmdstanpy - INFO - Chain [1] done processing
20:50:48 - cmdstanpy - INFO - Chain [1] start processing
20:50:48 - cmdstanpy - INFO - Chain [1] done processing
20:50:51 - cmdstanpy - INFO - Chain [1] start processing
20:50:52 - cmdstanpy - INFO - Chain [1] done processing
20:50:54 - cmdstanpy - INFO - Chain [1] start processing
20:50:55 - cmdstanpy - INFO - Chain [1] done processing
20:50:57 - cmdstanpy - INFO - Chain [1] start processing
20:50:58 - cmdstanpy - INFO - Chain [1] done processing
20:51:01 - cmdstanpy - INFO - Chain [1] start processing
20:51:01 - cmdstanpy - INFO - Chain [1] done processing
20:51:03 - cmdstanpy - INFO - Chain [1] start processing
20:51:04 - cmdstanpy - INFO - Chain [1] done processing
20:51:07 - cmdstanpy - INFO - Chain [1] start processing
20:51:07 - cmdstanpy - INFO - Chain [1]

20:54:13 - cmdstanpy - INFO - Chain [1] done processing
20:54:15 - cmdstanpy - INFO - Chain [1] start processing
20:54:16 - cmdstanpy - INFO - Chain [1] done processing
20:54:18 - cmdstanpy - INFO - Chain [1] start processing
20:54:19 - cmdstanpy - INFO - Chain [1] done processing
20:54:21 - cmdstanpy - INFO - Chain [1] start processing
20:54:21 - cmdstanpy - INFO - Chain [1] done processing
20:54:24 - cmdstanpy - INFO - Chain [1] start processing
20:54:24 - cmdstanpy - INFO - Chain [1] done processing
20:54:26 - cmdstanpy - INFO - Chain [1] start processing
20:54:27 - cmdstanpy - INFO - Chain [1] done processing
20:54:29 - cmdstanpy - INFO - Chain [1] start processing
20:54:29 - cmdstanpy - INFO - Chain [1] done processing
20:54:32 - cmdstanpy - INFO - Chain [1] start processing
20:54:32 - cmdstanpy - INFO - Chain [1] done processing
20:54:35 - cmdstanpy - INFO - Chain [1] start processing
20:54:35 - cmdstanpy - INFO - Chain [1] done processing
20:54:38 - cmdstanpy - INFO - Chain [1] 

In [47]:
silver_pred =pd.DataFrame(index= silver['ds'][-silver_forecasting_horizon:], columns=columns)
silver_pred['Actual'] = list(silver['y'][silver.shape[0]-silver_forecasting_horizon:])
silver_pred['ARIMA'] = arima_preds10
silver_pred['ARIMA-GARCH'] = arch_preds10
silver_pred['ARIMA 2'] = arima_preds2_10
silver_pred['ARIMA-GARCH 2'] = arch_preds2_10
silver_pred['ARIMA 3'] = arima_preds3_10
silver_pred['ARIMA-GARCH 3'] = arch_preds3_10
silver_pred['Simple Exponential Smoothing'] = ses_preds10
silver_pred['Holt\'s Exponential Smoothing'] = holt_preds10
silver_pred['Holt-Winter\'s Exponential Smoothing'] = hw_preds10
silver_pred['Prophet'] = prophet_preds10
silver_pred['Prophet+ARIMA'] = prophet_arima_preds10
silver_pred.to_csv('./results/silver_10step_forecasting.csv')

In [48]:
results.to_csv('./results/mae.csv')

### Platinum (1 step)

In [49]:
#ARIMA(2,1,2)
arima_errors = []
arima_preds1 = []
#ARIMA(2,1,2)-GARCH(1,1)
arch_errors = []
arch_preds1 = []
order = (2,1,2)


for i in range(platinum_forecasting_horizon) :
    arima_model = ARIMA(platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=1).to_numpy().item()
    arima_error = arima_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds1.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=1).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=1)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds1.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA'].iloc[6] = arima
results['ARIMA-GARCH'].iloc[6] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 53372.25066633611
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8923.587956180863
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5937.836129710597
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5631.408943109313
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5575.862234172395
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5575.635681130256
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5575.561853737519
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5575.556625948686
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5575.556551552496
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5575.556551552251
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5575.556551552496
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 53471.27974390115
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8931.191510266119
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5941.923742302541
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5635.993725808461
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5579.742974586971
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5579.520114414878
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5579.450960169528
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5579.44620680849
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5579.446144875692
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5579.446144875459
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5579.446144875692
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  war

Iteration:      1,   Func. Count:      6,   Neg. LLF: 53581.01484746051
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8939.41665676326
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5947.400715303819
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5637.889933814996
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5583.132770957081
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5582.9179782069705
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5582.874665296246
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5582.872146624626
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5582.872127084378
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5582.872127084358
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5582.872127084378
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 53586.57891453243

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 55887.84383788433
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9898.722182429516
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6645.829478032864
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6309.5322554372815
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6249.62705517619
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6249.215980909864
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6249.092504570186
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6249.0573701843805
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6249.055852571515
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6249.055823834924
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6249.055819755651
Iteration:     12,   Func. Count:     66,   Neg. LLF: 6249.055819755633
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6249.055819755651
            Iterations: 12


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 55978.079270191185
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9913.124306172609
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6633.541508940195
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6321.724247888044
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6256.328118228515
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6255.808850491153
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6255.697017700459
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6255.571792082889
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6255.563465974975
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6255.563205669729
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6255.563203606238
Iteration:     12,   Func. Count:     66,   Neg. LLF: 6255.563203605432
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6255.563203606238
            Iterations: 12


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [50]:
#ARIMA(0,1,0)
arima_errors = []
arima_preds2_1 = []
#ARIMA(0,1,0)-GARCH(1,1)
arch_errors = []
arch_preds2_1 = []
order = (0,1,0)


for i in range(platinum_forecasting_horizon) :
    arima_model = ARIMA(platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=1).to_numpy().item()
    arima_error = arima_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds2_1.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=1).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=1)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1].item()
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds2_1.append(arch_pred)
    arch_errors.append(arch_abs_error)


    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 2'].iloc[6] = arima
results['ARIMA-GARCH 2'].iloc[6] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 52929.590974819985
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8931.214495899574
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5950.457535088422
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5645.080050678637
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5586.344610915805
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5586.105563210034
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5585.910795153057
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5585.887058725546
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5585.886042640215
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5585.886036660619
Iteration:     11,   Func. Count:     61,   Neg. LLF: 5585.886036660429
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5585.886036660619
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 1

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      3,   Func. Count:     20,   Neg. LLF: 5958.730667538372
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5653.772886496607
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5594.212117821565
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5593.946360932987
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5593.796016423429
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5593.777905669795
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5593.7772964842125
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5593.7772930683495
Iteration:     11,   Func. Count:     61,   Neg. LLF: 5593.777293067904
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5593.7772930683495
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 11


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 53062.49541831744
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8950.641310158206
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5963.527795998294
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5658.166847525518
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5598.551891840393
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5598.291420253575
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5598.1314564501945
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5598.112186651773
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5598.111502813491
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5598.111499043663
Iteration:     11,   Func. Count:     61,   Neg. LLF: 5598.111499043325
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5598.111499043663
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 1

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55612.035349295795
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9867.416549351254
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6628.029089197915
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6287.232124577224
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6234.017979953382
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6233.377222085615
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6233.316510536564
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6233.314617906211
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6233.313210736059
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6233.313209342379
Iteration:     11,   Func. Count:     61,   Neg. LLF: 6233.313209342279
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6233.313209342379
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 1

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55839.27989968263
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9892.933891651053
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6644.211444447333
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6308.223128019979
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6249.50373331177
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6248.8932823187015
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6248.807737218938
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6248.784493852172
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6248.783572855529
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6248.783514645772
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6248.783509686411
Iteration:     12,   Func. Count:     66,   Neg. LLF: 6248.783509686462
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6248.783509686411
            Iterations: 12
 

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

In [51]:
#ARIMA(1,1,0)
arima_errors = []
arima_preds3_1 = []
#ARIMA(1,1,0)-GARCH(1,1)
arch_errors = []
arch_preds3_1 = []
order = (1,1,0)


for i in range(platinum_forecasting_horizon) :
    arima_model = ARIMA(platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=1).to_numpy().item()
    arima_error = arima_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds3_1.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=1).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=1)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1].item()
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds3_1.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 3'].iloc[6] = arima
results['ARIMA-GARCH 3'].iloc[6] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 53032.8848671239
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8931.563277868037
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5950.212460773453
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5642.08720946707
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5586.199743656929
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5585.89663936384
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5585.790909944656
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5585.778984051339
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5585.778722340518
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5585.778720758199
Iteration:     11,   Func. Count:     61,   Neg. LLF: 5585.778720757885
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5585.778720758199
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 11
It

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 53218.35126462803
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8946.30373968759
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5958.511020487794
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5650.722857779379
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5594.041746223262
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5593.737861433514
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5593.653564521869
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5593.64459862909
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5593.644441141328
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5593.64444114174
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5593.644441141328
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 53189.013711160515
I

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 53256.171220658376
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8957.071804038733
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5967.524613673755
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5659.713791500109
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5602.066400338388
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5601.781731885967
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5601.686845794117
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5601.676752580992
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5601.676549270261
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5601.67654876065
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5601.67654876065
            Iterations: 10
            Function evaluations: 57
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 53305.96173266686


...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 55852.0611340067
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9886.658403057432
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6639.509142103075
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6301.1184207030765
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6245.723759822091
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6245.114871298745
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6245.052378590155
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6245.048730816759
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6245.047871015255
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6245.047862507673
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6245.04785983928
Iteration:     12,   Func. Count:     66,   Neg. LLF: 6245.047859839285
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6245.04785983928
            Iterations: 12
   

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55990.328204366386
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9903.792319120024
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6652.240516851931
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6314.677062368719
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6257.009920691755
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6256.4330633650625
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6256.3684262388815
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6256.363370519013
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6256.362970177346
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6256.362962962743
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6256.362960652299
Iteration:     12,   Func. Count:     66,   Neg. LLF: 6256.362960652298
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6256.362960652299
            Iterations: 1

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [52]:
#SES
ses_errors = []
ses_preds1 = []
#Holt
holt_errors = []
holt_preds1 = []
#Holt-Winter
hw_errors = []
hw_preds1 = []

for i in range(platinum_forecasting_horizon) :
    ses_model = SimpleExpSmoothing(platinum['y'][:-platinum_forecasting_horizon+i])
    ses_model_fit = ses_model.fit()
    ses_pred = ses_model_fit.forecast(1).to_numpy().item()
    ses_error = ses_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    ses_abs_error = abs(ses_error)
    ses_preds1.append(ses_pred)
    ses_errors.append(ses_abs_error)
    
    holt_model = Holt(platinum['y'][:-platinum_forecasting_horizon+i])
    holt_model_fit = holt_model.fit()
    holt_pred = holt_model_fit.forecast(1).to_numpy().item()
    holt_error = holt_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    holt_abs_error = abs(holt_error)
    holt_preds1.append(holt_pred)
    holt_errors.append(holt_abs_error)
    
    hw_model = ExponentialSmoothing(platinum['y'][:-platinum_forecasting_horizon+i], seasonal_periods=5, trend='add', seasonal='add')
    hw_model_fit = hw_model.fit()
    hw_pred = hw_model_fit.forecast(1).to_numpy().item()
    hw_error = hw_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    hw_abs_error = abs(hw_error)
    hw_preds1.append(hw_pred)
    hw_errors.append(hw_abs_error)
    
ses_abs_errors = np.array(ses_errors)
ses = ses_abs_errors.mean()
holt_abs_errors = np.array(holt_errors)
holt = holt_abs_errors.mean()
hw_abs_errors = np.array(hw_errors)
hw = hw_abs_errors.mean()

results['Simple Exponential Smoothing'].iloc[6] = ses
results['Holt\'s Exponential Smoothing'].iloc[6] = holt
results['Holt-Winter\'s Exponential Smoothing'].iloc[6] = hw

In [53]:
#prophet
prophet_errors = []
prophet_preds1 = []
#prophet-ARIMA
prophet_arima_errors = []
prophet_arima_preds1 = []

for i in range(platinum_forecasting_horizon) :
    date = platinum['ds'].iloc[platinum.shape[0]-platinum_forecasting_horizon+i] - platinum['ds'].iloc[platinum.shape[0]-platinum_forecasting_horizon-1+i]
    m = Prophet()
    m.fit(platinum.iloc[:platinum.shape[0]-platinum_forecasting_horizon+i])
    future = m.make_future_dataframe(periods=date.days)
    forecast = m.predict(future)
    prophet_pred = forecast['yhat'].iloc[-1]
    prophet_error = prophet_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    prophet_abs_error = abs(prophet_error)
    prophet_preds1.append(prophet_pred)
    prophet_errors.append(prophet_abs_error)
    
    
    error_series = platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon+i] - forecast['yhat'].iloc[:-date.days]
    prophet_arima_model = pm.auto_arima(error_series, start_p = 0, start_q = 0, max_p = 5, max_q = 5, \
                                        seasonal = False, information_criteria = 'bic')
    prophet_arima_pred = prophet_arima_model.predict(n_periods=1).to_numpy().item() + prophet_pred
    prophet_arima_error = prophet_arima_pred- platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    prophet_arima_abs_error = abs(prophet_arima_error)
    prophet_arima_preds1.append(prophet_arima_pred)
    prophet_arima_errors.append(prophet_arima_abs_error)    

    
prophet_abs_errors = np.array(prophet_errors)
prophet = prophet_abs_errors.mean()
prophet_arima_abs_errors = np.array(prophet_arima_errors)
prophet_arima = prophet_arima_abs_errors.mean()

results['Prophet'].iloc[6] = prophet
results['Prophet+ARIMA'].iloc[6] = prophet_arima

21:01:10 - cmdstanpy - INFO - Chain [1] start processing
21:01:11 - cmdstanpy - INFO - Chain [1] done processing
21:01:13 - cmdstanpy - INFO - Chain [1] start processing
21:01:13 - cmdstanpy - INFO - Chain [1] done processing
21:01:15 - cmdstanpy - INFO - Chain [1] start processing
21:01:16 - cmdstanpy - INFO - Chain [1] done processing
21:01:18 - cmdstanpy - INFO - Chain [1] start processing
21:01:18 - cmdstanpy - INFO - Chain [1] done processing
21:01:20 - cmdstanpy - INFO - Chain [1] start processing
21:01:21 - cmdstanpy - INFO - Chain [1] done processing
21:01:23 - cmdstanpy - INFO - Chain [1] start processing
21:01:23 - cmdstanpy - INFO - Chain [1] done processing
21:01:25 - cmdstanpy - INFO - Chain [1] start processing
21:01:25 - cmdstanpy - INFO - Chain [1] done processing
21:01:28 - cmdstanpy - INFO - Chain [1] start processing
21:01:28 - cmdstanpy - INFO - Chain [1] done processing
21:01:30 - cmdstanpy - INFO - Chain [1] start processing
21:01:30 - cmdstanpy - INFO - Chain [1]

21:03:20 - cmdstanpy - INFO - Chain [1] done processing
21:03:21 - cmdstanpy - INFO - Chain [1] start processing
21:03:22 - cmdstanpy - INFO - Chain [1] done processing
21:03:24 - cmdstanpy - INFO - Chain [1] start processing
21:03:24 - cmdstanpy - INFO - Chain [1] done processing
21:03:26 - cmdstanpy - INFO - Chain [1] start processing
21:03:26 - cmdstanpy - INFO - Chain [1] done processing
21:03:28 - cmdstanpy - INFO - Chain [1] start processing
21:03:28 - cmdstanpy - INFO - Chain [1] done processing
21:03:29 - cmdstanpy - INFO - Chain [1] start processing
21:03:30 - cmdstanpy - INFO - Chain [1] done processing
21:03:31 - cmdstanpy - INFO - Chain [1] start processing
21:03:31 - cmdstanpy - INFO - Chain [1] done processing
21:03:32 - cmdstanpy - INFO - Chain [1] start processing
21:03:33 - cmdstanpy - INFO - Chain [1] done processing
21:03:34 - cmdstanpy - INFO - Chain [1] start processing
21:03:35 - cmdstanpy - INFO - Chain [1] done processing
21:03:37 - cmdstanpy - INFO - Chain [1] 

21:05:29 - cmdstanpy - INFO - Chain [1] done processing
21:05:30 - cmdstanpy - INFO - Chain [1] start processing
21:05:30 - cmdstanpy - INFO - Chain [1] done processing
21:05:31 - cmdstanpy - INFO - Chain [1] start processing
21:05:31 - cmdstanpy - INFO - Chain [1] done processing
21:05:33 - cmdstanpy - INFO - Chain [1] start processing
21:05:33 - cmdstanpy - INFO - Chain [1] done processing
21:05:34 - cmdstanpy - INFO - Chain [1] start processing
21:05:34 - cmdstanpy - INFO - Chain [1] done processing
21:05:35 - cmdstanpy - INFO - Chain [1] start processing
21:05:36 - cmdstanpy - INFO - Chain [1] done processing
21:05:37 - cmdstanpy - INFO - Chain [1] start processing
21:05:37 - cmdstanpy - INFO - Chain [1] done processing
21:05:38 - cmdstanpy - INFO - Chain [1] start processing
21:05:38 - cmdstanpy - INFO - Chain [1] done processing
21:05:40 - cmdstanpy - INFO - Chain [1] start processing
21:05:40 - cmdstanpy - INFO - Chain [1] done processing
21:05:41 - cmdstanpy - INFO - Chain [1] 

In [54]:
platinum_pred =pd.DataFrame(index= platinum['ds'][-platinum_forecasting_horizon:], columns=columns)
platinum_pred['Actual'] = list(platinum['y'][platinum.shape[0]-platinum_forecasting_horizon:])
platinum_pred['ARIMA'] = arima_preds1
platinum_pred['ARIMA-GARCH'] = arch_preds1
platinum_pred['ARIMA 2'] = arima_preds2_1
platinum_pred['ARIMA-GARCH 2'] = arch_preds2_1
platinum_pred['ARIMA 3'] = arima_preds3_1
platinum_pred['ARIMA-GARCH 3'] = arch_preds3_1
platinum_pred['Simple Exponential Smoothing'] = ses_preds1
platinum_pred['Holt\'s Exponential Smoothing'] = holt_preds1
platinum_pred['Holt-Winter\'s Exponential Smoothing'] = hw_preds1
platinum_pred['Prophet'] = prophet_preds1
platinum_pred['Prophet+ARIMA'] = prophet_arima_preds1
platinum_pred.to_csv('./results/platinum_1step_forecasting.csv')

In [55]:
results.to_csv('./results/mae.csv')

### Platinum (5 step)

In [56]:
#ARIMA(2,1,2)
arima_errors = []
arima_preds5 = []
#ARIMA(2,1,2)-GARCH(1,1)
arch_errors = []
arch_preds5 = []
order = (2,1,2)


for i in range(platinum_forecasting_horizon) :
    arima_model = ARIMA(platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon-4+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=5).iloc[-1].item()
    arima_error = arima_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds5.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=5).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=5)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds5.append(arch_pred)
    arch_errors.append(arch_abs_error)
    

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()


results['ARIMA'].iloc[7] = arima
results['ARIMA-GARCH'].iloc[7] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 52974.696188629634
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8911.844887870819
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5923.583056493575
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5628.033032130319
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5569.749586298934
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5569.3690131615585
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5569.28622970404
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5569.276271742578
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5569.276087814515
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5569.276086894513
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5569.276086894513
            Iterations: 10
            Function evaluations: 57
            Gradient evaluations: 10


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 53375.702921045115
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8906.472641359353
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5923.449830471196
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5616.367050700124
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5562.345191647411
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5562.112763328823
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5562.062308864871
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5562.058954982915
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5562.058924179584
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5562.058924179575
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5562.058924179584
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 53117.70927893983
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8908.745773819084
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5929.711438384789
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5622.2621063928345
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5568.324790505649
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5568.085865822801
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5568.005907987932
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5567.999809244266
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5567.99971673377
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5567.9997167334395
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5567.99971673377
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10


...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 55762.252937989746
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9884.624990326509
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6612.614769074497
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6295.930507519073
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6237.6103557604865
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6237.019929275431
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6236.9258499365005
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6236.82290155044
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6236.81752084984
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6236.817377955147
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6236.81737394089
Iteration:     12,   Func. Count:     66,   Neg. LLF: 6236.8173739397835
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6236.81737394089
            Iterations: 12
 

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 55741.07827383738
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9880.092801330778
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6633.5554287887535
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6295.050016769486
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6238.147660841705
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6237.700892750778
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6237.594123115992
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6237.567472756477
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6237.566524889266
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6237.566500419747
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6237.56649689667
Iteration:     12,   Func. Count:     66,   Neg. LLF: 6237.5664968966685
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6237.56649689667
            Iterations: 12
 

C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [57]:
#ARIMA(0,1,0)
arima_errors = []
arima_preds2_5 = []
#ARIMA(0,1,0)-GARCH(1,1)
arch_errors = []
arch_preds2_5 = []
order = (0,1,0)


for i in range(platinum_forecasting_horizon) :
    arima_model = ARIMA(platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon-4+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=5).iloc[-1].item()
    arima_error = arima_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds2_5.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=5).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=5)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds2_5.append(arch_pred)
    arch_errors.append(arch_abs_error)


    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 2'].iloc[7] = arima
results['ARIMA-GARCH 2'].iloc[7] = arch

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 52895.71206293313
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8909.893743146871
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5930.570296713653
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5626.565096774821
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5569.269757174474
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5569.040176453082
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5568.830855506778
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5568.804628284551
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5568.803413585918
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5568.803404880466
Iteration:     11,   Func. Count:     61,   Neg. LLF: 5568.803404880142
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5568.803404880466
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 11

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 52929.590974819985
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8931.214495899574
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5950.457535088422
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5645.080050678637
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5586.344610915805
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5586.105563210034
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5585.910795153057
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5585.887058725546
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5585.886042640215
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5585.886036660619
Iteration:     11,   Func. Count:     61,   Neg. LLF: 5585.886036660429
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5585.886036660619
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 1

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55664.10700526905
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9838.315486020772
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6610.795608652277
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6270.369904865183
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6215.048071827843
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6214.493617705983
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6214.434573208542
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6214.429700469549
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6214.429666202854
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6214.429655342723
Iteration:     11,   Func. Count:     61,   Neg. LLF: 6214.429655342816
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6214.429655342723
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 11

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55612.035349295795
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9867.416549351254
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6628.029089197915
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6287.232124577224
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6234.017979953382
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6233.377222085615
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6233.316510536564
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6233.314617906211
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6233.313210736059
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6233.313209342379
Iteration:     11,   Func. Count:     61,   Neg. LLF: 6233.313209342279
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6233.313209342379
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 1

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

In [58]:
#ARIMA(1,1,0)
arima_errors = []
arima_preds3_5 = []
#ARIMA(1,1,0)-GARCH(1,1)
arch_errors = []
arch_preds3_5 = []
order = (1,1,0)


for i in range(platinum_forecasting_horizon) :
    arima_model = ARIMA(platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon-4+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=5).iloc[-1].item()
    arima_error = arima_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds3_5.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=5).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=5)
    predicted_et = garch_forecast.mean['h.1'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds3_5.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 3'].iloc[7] = arima
results['ARIMA-GARCH 3'].iloc[7] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 52993.67627134522
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8910.074464216359
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5930.433328740956
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5623.899810742145
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5569.149778375409
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5568.802595884287
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5568.729237351838
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5568.721363975742
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5568.721242471984
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5568.7212424726295
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5568.721242471984
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 52960.6517902754

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 52930.12385254
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8924.167210899099
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5946.176783334064
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5637.373920742464
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5582.319971513768
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5582.010492153303
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5581.89651602298
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5581.883361190036
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5581.883057248435
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5581.883056451101
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5581.883056451101
            Iterations: 10
            Function evaluations: 57
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 53032.8848671239
Iter

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      3,   Func. Count:     20,   Neg. LLF: 5954.355773880785
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5646.632762790349
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5589.9784573233255
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5589.673860105595
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5589.58683865094
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5589.577484530424
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5589.577316257042
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5589.577316257437
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5589.577316257042
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 53218.35126462803
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8946.30373968759
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5958.511020487794


...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55747.79628300558
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9843.78261792499
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6614.694483490027
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6273.061833787149
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6219.082693722454
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6218.5910619674
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6218.511165351836
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6218.50037055548
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6218.5002080253535
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6218.500191917734
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6218.500190696972
Iteration:     12,   Func. Count:     66,   Neg. LLF: 6218.500190697097
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6218.500190696972
            Iterations: 12
    

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55723.17589528287
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9868.24887813017
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6627.336061471161
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6285.082073347948
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6234.07570470574
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6233.48312947195
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6233.417507772511
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6233.412336201545
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6233.412258459099
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6233.412230757648
Iteration:     11,   Func. Count:     61,   Neg. LLF: 6233.41223075882
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6233.412230757648
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 11
Ite

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [59]:
#SES
ses_errors = []
ses_preds5 = []
#Holt
holt_errors = []
holt_preds5 = []
#Holt-Winter
hw_errors = []
hw_preds5 = []

for i in range(platinum_forecasting_horizon) :
    ses_model = SimpleExpSmoothing(platinum['y'][:-platinum_forecasting_horizon-4+i])
    ses_model_fit = ses_model.fit()
    ses_pred = ses_model_fit.forecast(5).iloc[-1].item()
    ses_error = ses_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    ses_abs_error = abs(ses_error)
    ses_preds5.append(ses_pred)
    ses_errors.append(ses_abs_error)
    
    holt_model = Holt(platinum['y'][:-platinum_forecasting_horizon-4+i])
    holt_model_fit = holt_model.fit()
    holt_pred = holt_model_fit.forecast(5).iloc[-1].item()
    holt_error = holt_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    holt_abs_error = abs(holt_error)
    holt_preds5.append(holt_pred)
    holt_errors.append(holt_abs_error)
    
    hw_model = ExponentialSmoothing(platinum['y'][:-platinum_forecasting_horizon-4+i], seasonal_periods=5, trend='add', seasonal='add')
    hw_model_fit = hw_model.fit()
    hw_pred = hw_model_fit.forecast(5).iloc[-1].item()
    hw_error = hw_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    hw_abs_error = abs(hw_error)
    hw_preds5.append(hw_pred)
    hw_errors.append(hw_abs_error)
    
ses_abs_errors = np.array(ses_errors)
ses = ses_abs_errors.mean()
holt_abs_errors = np.array(holt_errors)
holt = holt_abs_errors.mean()
hw_abs_errors = np.array(hw_errors)
hw = hw_abs_errors.mean()

results['Simple Exponential Smoothing'].iloc[7] = ses
results['Holt\'s Exponential Smoothing'].iloc[7] = holt
results['Holt-Winter\'s Exponential Smoothing'].iloc[7] = hw

In [60]:
#prophet
prophet_errors = []
prophet_preds5 = []
#prophet-ARIMA
prophet_arima_errors = []
prophet_arima_preds5 = []

for i in range(platinum_forecasting_horizon) :
    date = platinum['ds'].iloc[platinum.shape[0]-platinum_forecasting_horizon+i] - platinum['ds'].iloc[platinum.shape[0]-platinum_forecasting_horizon-5+i]
    m = Prophet()
    m.fit(platinum.iloc[:platinum.shape[0]-platinum_forecasting_horizon-4+i])
    future = m.make_future_dataframe(periods=date.days)
    forecast = m.predict(future)
    prophet_pred = forecast['yhat'].iloc[-1]
    prophet_error = prophet_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    prophet_abs_error = abs(prophet_error)
    prophet_preds5.append(prophet_pred)
    prophet_errors.append(prophet_abs_error)
    
    
    error_series = platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon-4+i] - forecast['yhat'].iloc[:-date.days]
    prophet_arima_model = pm.auto_arima(error_series, start_p = 0, start_q = 0, max_p = 5, max_q = 5, \
                                        seasonal = False, information_criteria = 'bic')
    prophet_arima_pred = prophet_arima_model.predict(n_periods=5).iloc[-1].item() + prophet_pred
    prophet_arima_error = prophet_arima_pred- platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    prophet_arima_abs_error = abs(prophet_arima_error)
    prophet_arima_preds5.append(prophet_arima_pred)
    prophet_arima_errors.append(prophet_arima_abs_error)    

    
prophet_abs_errors = np.array(prophet_errors)
prophet = prophet_abs_errors.mean()
prophet_arima_abs_errors = np.array(prophet_arima_errors)
prophet_arima = prophet_arima_abs_errors.mean()

results['Prophet'].iloc[7] = prophet
results['Prophet+ARIMA'].iloc[7] = prophet_arima

21:09:14 - cmdstanpy - INFO - Chain [1] start processing
21:09:14 - cmdstanpy - INFO - Chain [1] done processing
21:09:16 - cmdstanpy - INFO - Chain [1] start processing
21:09:16 - cmdstanpy - INFO - Chain [1] done processing
21:09:18 - cmdstanpy - INFO - Chain [1] start processing
21:09:19 - cmdstanpy - INFO - Chain [1] done processing
21:09:20 - cmdstanpy - INFO - Chain [1] start processing
21:09:21 - cmdstanpy - INFO - Chain [1] done processing
21:09:22 - cmdstanpy - INFO - Chain [1] start processing
21:09:23 - cmdstanpy - INFO - Chain [1] done processing
21:09:24 - cmdstanpy - INFO - Chain [1] start processing
21:09:25 - cmdstanpy - INFO - Chain [1] done processing
21:09:27 - cmdstanpy - INFO - Chain [1] start processing
21:09:27 - cmdstanpy - INFO - Chain [1] done processing
21:09:29 - cmdstanpy - INFO - Chain [1] start processing
21:09:29 - cmdstanpy - INFO - Chain [1] done processing
21:09:31 - cmdstanpy - INFO - Chain [1] start processing
21:09:31 - cmdstanpy - INFO - Chain [1]

21:11:18 - cmdstanpy - INFO - Chain [1] done processing
21:11:19 - cmdstanpy - INFO - Chain [1] start processing
21:11:19 - cmdstanpy - INFO - Chain [1] done processing
21:11:21 - cmdstanpy - INFO - Chain [1] start processing
21:11:21 - cmdstanpy - INFO - Chain [1] done processing
21:11:22 - cmdstanpy - INFO - Chain [1] start processing
21:11:22 - cmdstanpy - INFO - Chain [1] done processing
21:11:24 - cmdstanpy - INFO - Chain [1] start processing
21:11:25 - cmdstanpy - INFO - Chain [1] done processing
21:11:26 - cmdstanpy - INFO - Chain [1] start processing
21:11:26 - cmdstanpy - INFO - Chain [1] done processing
21:11:28 - cmdstanpy - INFO - Chain [1] start processing
21:11:29 - cmdstanpy - INFO - Chain [1] done processing
21:11:30 - cmdstanpy - INFO - Chain [1] start processing
21:11:31 - cmdstanpy - INFO - Chain [1] done processing
21:11:32 - cmdstanpy - INFO - Chain [1] start processing
21:11:32 - cmdstanpy - INFO - Chain [1] done processing
21:11:34 - cmdstanpy - INFO - Chain [1] 

21:13:32 - cmdstanpy - INFO - Chain [1] done processing
21:13:33 - cmdstanpy - INFO - Chain [1] start processing
21:13:33 - cmdstanpy - INFO - Chain [1] done processing
21:13:34 - cmdstanpy - INFO - Chain [1] start processing
21:13:35 - cmdstanpy - INFO - Chain [1] done processing
21:13:36 - cmdstanpy - INFO - Chain [1] start processing
21:13:36 - cmdstanpy - INFO - Chain [1] done processing
21:13:37 - cmdstanpy - INFO - Chain [1] start processing
21:13:37 - cmdstanpy - INFO - Chain [1] done processing
21:13:38 - cmdstanpy - INFO - Chain [1] start processing
21:13:39 - cmdstanpy - INFO - Chain [1] done processing
21:13:40 - cmdstanpy - INFO - Chain [1] start processing
21:13:40 - cmdstanpy - INFO - Chain [1] done processing
21:13:41 - cmdstanpy - INFO - Chain [1] start processing
21:13:42 - cmdstanpy - INFO - Chain [1] done processing
21:13:43 - cmdstanpy - INFO - Chain [1] start processing
21:13:43 - cmdstanpy - INFO - Chain [1] done processing
21:13:44 - cmdstanpy - INFO - Chain [1] 

In [61]:
platinum_pred =pd.DataFrame(index= platinum['ds'][-platinum_forecasting_horizon:], columns=columns)
platinum_pred['Actual'] = list(platinum['y'][platinum.shape[0]-platinum_forecasting_horizon:])
platinum_pred['ARIMA'] = arima_preds5
platinum_pred['ARIMA-GARCH'] = arch_preds5
platinum_pred['ARIMA 2'] = arima_preds2_5
platinum_pred['ARIMA-GARCH 2'] = arch_preds2_5
platinum_pred['ARIMA 3'] = arima_preds3_5
platinum_pred['ARIMA-GARCH 3'] = arch_preds3_5
platinum_pred['Simple Exponential Smoothing'] = ses_preds5
platinum_pred['Holt\'s Exponential Smoothing'] = holt_preds5
platinum_pred['Holt-Winter\'s Exponential Smoothing'] = hw_preds5
platinum_pred['Prophet'] = prophet_preds5
platinum_pred['Prophet+ARIMA'] = prophet_arima_preds5
platinum_pred.to_csv('./results/platinum_5step_forecasting.csv')

In [62]:
results.to_csv('./results/mae.csv')

### Platinum (10 step)

In [63]:
#ARIMA(2,1,2)
arima_errors = []
arima_preds10 = []
#ARIMA(2,1,2)-GARCH(1,1)
arch_errors = []
arch_preds10 = []
order = (2,1,2)


for i in range(platinum_forecasting_horizon) :
    arima_model = ARIMA(platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon-9+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=10).iloc[-1].item()
    arima_error = arima_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds10.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=10).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=10)
    predicted_et = garch_forecast.mean['h.01'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds10.append(arch_pred)
    arch_errors.append(arch_abs_error)
    

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()


results['ARIMA'].iloc[8] = arima
results['ARIMA-GARCH'].iloc[8] = arch

C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zeros as starting parameters.
  warn('Non-invertible starting MA parameters found.'
C:\Users\Seungyun\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from 

Iteration:      1,   Func. Count:      6,   Neg. LLF: 52959.7270755245
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8864.40250769164
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5898.138626967157
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5583.69388237903
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5537.11828469851
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5536.856845403239
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5536.823187114246
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5536.821486620456
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5536.821479419808
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5536.821479419725
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5536.821479419808
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 53096.77774294594
Ite

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 52971.7026698917
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8886.990921233108
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5913.50421974967
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5604.26789382693
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5553.1224951344575
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5552.918312194446
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5552.5731309248495
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5552.528386267726
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5552.525501066033
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5552.525455558818
Iteration:     11,   Func. Count:     62,   Neg. LLF: 5552.525453980632
Iteration:     12,   Func. Count:     66,   Neg. LLF: 5552.5254539809985
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5552.525453980632
            Iterations: 12
 

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 55719.27467888369
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9839.347825938894
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6607.907840259137
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6267.443790709021
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6211.174292911121
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6210.7475717486195
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6210.691360776422
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6210.687219388261
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6210.687151588368
Iteration:     10,   Func. Count:     56,   Neg. LLF: 6210.687151586467
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6210.687151588368
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      1,   Func. Count:      6,   Neg. LLF: 55716.84270178637
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9843.815642503556
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6612.543805942152
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6272.203657241985
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6215.150101629898
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6214.733132972715
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6214.6706792086425
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6214.665388746838
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6214.665319641317
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6214.6653189915
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6214.6653189915
            Iterations: 10
            Function evaluations: 57
            Gradient evaluations: 10


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [64]:
#ARIMA(0,1,0)
arima_errors = []
arima_preds2_10 = []
#ARIMA(0,1,0)-GARCH(1,1)
arch_errors = []
arch_preds2_10 = []
order = (0,1,0)


for i in range(platinum_forecasting_horizon) :
    arima_model = ARIMA(platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon-9+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=10).iloc[-1].item()
    arima_error = arima_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds2_10.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=10).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=10)
    predicted_et = garch_forecast.mean['h.01'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds2_10.append(arch_pred)
    arch_errors.append(arch_abs_error)


    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 2'].iloc[8] = arima
results['ARIMA-GARCH 2'].iloc[8] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 52379.817704338304
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8869.65363608939
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5910.191588103169
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5599.828796110419
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5548.2241725601825
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5547.896916275235
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5547.731325995092
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5547.710282460732
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5547.70962471814
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5547.709621081827
Iteration:     11,   Func. Count:     61,   Neg. LLF: 5547.709621081798
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5547.709621081827
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 11

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 52712.31930447711
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8894.953965394243
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5922.4825840453805
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5616.121806228073
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5561.1898992564475
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5560.961621082803
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5560.718843354196
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5560.687647772842
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5560.686036451756
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5560.686021601023
Iteration:     11,   Func. Count:     61,   Neg. LLF: 5560.68602160089
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5560.686021601023
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 1

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


Iteration:      5,   Func. Count:     32,   Neg. LLF: 5565.27236912689
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5565.05398873541
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5564.816581380212
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5564.786513826617
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5564.784959094486
Iteration:     10,   Func. Count:     57,   Neg. LLF: 5564.784945711521
Iteration:     11,   Func. Count:     61,   Neg. LLF: 5564.784945711299
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5564.784945711521
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 11
Iteration:      1,   Func. Count:      6,   Neg. LLF: 52895.71206293313
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8909.893743146871
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5930.570296713653
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5626.565096774821
I

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55629.450727626456
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9799.916592617275
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6585.014158915005
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6245.402220930901
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6188.744064010483
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6188.199840062116
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6188.151622978536
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6188.149850141641
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6188.149703751607
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6188.149700624213
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6188.149699612046
Iteration:     12,   Func. Count:     66,   Neg. LLF: 6188.149699611962
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6188.149699612046
            Iterations: 12


C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55681.53170506735
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9821.833153487021
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6602.355395504877
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6262.138568352486
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6204.900407757274
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6204.366892710888
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6204.320615489185
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6204.318983793157
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6204.318809324529
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6204.318805743912
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6204.3188050402405
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6204.3188050402405
            Iterations: 11
            Function evaluations: 62
            Gradient evaluations: 

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

In [65]:
print(arch)

41.98123248381454


In [66]:
#ARIMA(1,1,0)
arima_errors = []
arima_preds3_10 = []
#ARIMA(1,1,0)-GARCH(1,1)
arch_errors = []
arch_preds3_10 = []
order = (1,1,0)


for i in range(platinum_forecasting_horizon) :
    arima_model = ARIMA(platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon-9+i], order = order)
    arima_model_fit = arima_model.fit()
    arima_pred = arima_model_fit.forecast(steps=10).iloc[-1].item()
    arima_error = arima_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arima_abs_error = abs(arima_error)
    arima_preds3_10.append(arima_pred)
    arima_errors.append(arima_abs_error)
    
    arima_residuals = arima_model_fit.resid
    garch = arch_model(arima_residuals, p=1,q=1)
    garch_fitted = garch.fit()
    predicted_mu = arima_model_fit.predict(n_periods=10).iloc[-1]
    garch_forecast = garch_fitted.forecast(horizon=10)
    predicted_et = garch_forecast.mean['h.01'].iloc[-1]
    arch_pred = predicted_mu + predicted_et
    arch_error = arch_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    arch_abs_error = abs(arch_error)
    arch_preds3_10.append(arch_pred)
    arch_errors.append(arch_abs_error)

    
arima_abs_errors = np.array(arima_errors)
arima = arima_abs_errors.mean()
arch_abs_errors = np.array(arch_errors)
arch = arch_abs_errors.mean()

results['ARIMA 3'].iloc[8] = arima
results['ARIMA-GARCH 3'].iloc[8] = arch

Iteration:      1,   Func. Count:      6,   Neg. LLF: 52475.27367681811
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8870.132263910233
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5910.027083190063
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5597.531385506043
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5548.145945564558
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5547.758319873484
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5547.672570598355
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5547.663871465203
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5547.663755427713
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5547.663755428059
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5547.663755427713
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 52617.30624337676

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      6,   Func. Count:     37,   Neg. LLF: 5556.612183819295
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5556.5123335271455
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5556.500896279271
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5556.500695975463
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5556.500695975626
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5556.500695975463
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 52807.214636215045
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8895.208506008563
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5922.324283438304
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5613.64445876446
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5561.094933378316
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5560.74305877363

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 52993.67627134522
Iteration:      2,   Func. Count:     13,   Neg. LLF: 8910.074464216359
Iteration:      3,   Func. Count:     20,   Neg. LLF: 5930.433328740956
Iteration:      4,   Func. Count:     26,   Neg. LLF: 5623.899810742145
Iteration:      5,   Func. Count:     32,   Neg. LLF: 5569.149778375409
Iteration:      6,   Func. Count:     37,   Neg. LLF: 5568.802595884287
Iteration:      7,   Func. Count:     42,   Neg. LLF: 5568.729237351838
Iteration:      8,   Func. Count:     47,   Neg. LLF: 5568.721363975742
Iteration:      9,   Func. Count:     52,   Neg. LLF: 5568.721242471984
Iteration:     10,   Func. Count:     56,   Neg. LLF: 5568.7212424726295
Optimization terminated successfully    (Exit mode 0)
            Current function value: 5568.721242471984
            Iterations: 10
            Function evaluations: 56
            Gradient evaluations: 10
Iteration:      1,   Func. Count:      6,   Neg. LLF: 52960.6517902754

...

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55810.28967348725
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9818.080013089622
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6597.263175659652
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6255.397040067988
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6200.615451867687
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6200.149446674592
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6200.082687284328
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6200.074984435651
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6200.074898383848
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6200.074885289598
Iteration:     11,   Func. Count:     61,   Neg. LLF: 6200.0748852879615
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6200.074885289598
            Iterations: 11
            Function evaluations: 61
            Gradient evaluations: 1

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(
C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence t

Iteration:      1,   Func. Count:      6,   Neg. LLF: 55749.452931962864
Iteration:      2,   Func. Count:     13,   Neg. LLF: 9839.133332307085
Iteration:      3,   Func. Count:     20,   Neg. LLF: 6610.113607123942
Iteration:      4,   Func. Count:     26,   Neg. LLF: 6268.167911358691
Iteration:      5,   Func. Count:     32,   Neg. LLF: 6215.11653104794
Iteration:      6,   Func. Count:     37,   Neg. LLF: 6214.648059747971
Iteration:      7,   Func. Count:     42,   Neg. LLF: 6214.548389190519
Iteration:      8,   Func. Count:     47,   Neg. LLF: 6214.5334215312505
Iteration:      9,   Func. Count:     52,   Neg. LLF: 6214.533091871982
Iteration:     10,   Func. Count:     57,   Neg. LLF: 6214.5330799581125
Iteration:     11,   Func. Count:     62,   Neg. LLF: 6214.533077502618
Iteration:     12,   Func. Count:     66,   Neg. LLF: 6214.5330775028215
Optimization terminated successfully    (Exit mode 0)
            Current function value: 6214.533077502618
            Iterations: 1

C:\Users\Seungyun\anaconda3\lib\site-packages\arch\__future__\_utility.py:11: FutureWarning: 
The default for reindex is True. After September 2021 this will change to
False. Set reindex to True or False to silence this message. Alternatively,
you can use the import comment

from arch.__future__ import reindexing

to globally set reindex to True and silence this warning.

  warnings.warn(


In [67]:
#SES
ses_errors = []
ses_preds10 = []
#Holt
holt_errors = []
holt_preds10 = []
#Holt-Winter
hw_errors = []
hw_preds10 = []

for i in range(platinum_forecasting_horizon) :
    ses_model = SimpleExpSmoothing(platinum['y'][:-platinum_forecasting_horizon-9+i])
    ses_model_fit = ses_model.fit()
    ses_pred = ses_model_fit.forecast(10).iloc[-1].item()
    ses_error = ses_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    ses_abs_error = abs(ses_error)
    ses_preds10.append(ses_pred)
    ses_errors.append(ses_abs_error)
    
    holt_model = Holt(platinum['y'][:-platinum_forecasting_horizon-9+i])
    holt_model_fit = holt_model.fit()
    holt_pred = holt_model_fit.forecast(10).iloc[-1].item()
    holt_error = holt_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    holt_abs_error = abs(holt_error)
    holt_preds10.append(holt_pred)
    holt_errors.append(holt_abs_error)
    
    hw_model = ExponentialSmoothing(platinum['y'][:-platinum_forecasting_horizon-9+i], seasonal_periods=5, trend='add', seasonal='add')
    hw_model_fit = hw_model.fit()
    hw_pred = hw_model_fit.forecast(10).iloc[-1].item()
    hw_error = hw_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    hw_abs_error = abs(hw_error)
    hw_preds10.append(hw_pred)
    hw_errors.append(hw_abs_error)
    
ses_abs_errors = np.array(ses_errors)
ses = ses_abs_errors.mean()
holt_abs_errors = np.array(holt_errors)
holt = holt_abs_errors.mean()
hw_abs_errors = np.array(hw_errors)
hw = hw_abs_errors.mean()

results['Simple Exponential Smoothing'].iloc[8] = ses
results['Holt\'s Exponential Smoothing'].iloc[8] = holt
results['Holt-Winter\'s Exponential Smoothing'].iloc[8] = hw

In [68]:
#prophet
prophet_errors = []
prophet_preds10 = []
#prophet-ARIMA
prophet_arima_errors = []
prophet_arima_preds10 = []

for i in range(platinum_forecasting_horizon) :
    date = platinum['ds'].iloc[platinum.shape[0]-platinum_forecasting_horizon+i] - platinum['ds'].iloc[platinum.shape[0]-platinum_forecasting_horizon-10+i]
    m = Prophet()
    m.fit(platinum.iloc[:platinum.shape[0]-platinum_forecasting_horizon-9+i])
    future = m.make_future_dataframe(periods=date.days)
    forecast = m.predict(future)
    prophet_pred = forecast['yhat'].iloc[-1]
    prophet_error = prophet_pred - platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    prophet_abs_error = abs(prophet_error)
    prophet_preds10.append(prophet_pred)
    prophet_errors.append(prophet_abs_error)
    
    
    error_series = platinum['y'][:platinum.shape[0]-platinum_forecasting_horizon-9+i] - forecast['yhat'].iloc[:-date.days]
    prophet_arima_model = pm.auto_arima(error_series, start_p = 0, start_q = 0, max_p = 5, max_q = 5, \
                                        seasonal = False, information_criteria = 'bic')
    prophet_arima_pred = prophet_arima_model.predict(n_periods=10).iloc[-1].item() + prophet_pred
    prophet_arima_error = prophet_arima_pred- platinum['y'][platinum.shape[0]-platinum_forecasting_horizon+i]
    prophet_arima_abs_error = abs(prophet_arima_error)
    prophet_arima_preds10.append(prophet_arima_pred)
    prophet_arima_errors.append(prophet_arima_abs_error)    

    
prophet_abs_errors = np.array(prophet_errors)
prophet = prophet_abs_errors.mean()
prophet_arima_abs_errors = np.array(prophet_arima_errors)
prophet_arima = prophet_arima_abs_errors.mean()

results['Prophet'].iloc[8] = prophet
results['Prophet+ARIMA'].iloc[8] = prophet_arima

21:17:17 - cmdstanpy - INFO - Chain [1] start processing
21:17:17 - cmdstanpy - INFO - Chain [1] done processing
21:17:19 - cmdstanpy - INFO - Chain [1] start processing
21:17:19 - cmdstanpy - INFO - Chain [1] done processing
21:17:21 - cmdstanpy - INFO - Chain [1] start processing
21:17:21 - cmdstanpy - INFO - Chain [1] done processing
21:17:23 - cmdstanpy - INFO - Chain [1] start processing
21:17:23 - cmdstanpy - INFO - Chain [1] done processing
21:17:25 - cmdstanpy - INFO - Chain [1] start processing
21:17:25 - cmdstanpy - INFO - Chain [1] done processing
21:17:27 - cmdstanpy - INFO - Chain [1] start processing
21:17:27 - cmdstanpy - INFO - Chain [1] done processing
21:17:29 - cmdstanpy - INFO - Chain [1] start processing
21:17:29 - cmdstanpy - INFO - Chain [1] done processing
21:17:31 - cmdstanpy - INFO - Chain [1] start processing
21:17:31 - cmdstanpy - INFO - Chain [1] done processing
21:17:33 - cmdstanpy - INFO - Chain [1] start processing
21:17:33 - cmdstanpy - INFO - Chain [1]

21:19:21 - cmdstanpy - INFO - Chain [1] done processing
21:19:22 - cmdstanpy - INFO - Chain [1] start processing
21:19:22 - cmdstanpy - INFO - Chain [1] done processing
21:19:23 - cmdstanpy - INFO - Chain [1] start processing
21:19:24 - cmdstanpy - INFO - Chain [1] done processing
21:19:25 - cmdstanpy - INFO - Chain [1] start processing
21:19:25 - cmdstanpy - INFO - Chain [1] done processing
21:19:27 - cmdstanpy - INFO - Chain [1] start processing
21:19:27 - cmdstanpy - INFO - Chain [1] done processing
21:19:28 - cmdstanpy - INFO - Chain [1] start processing
21:19:28 - cmdstanpy - INFO - Chain [1] done processing
21:19:29 - cmdstanpy - INFO - Chain [1] start processing
21:19:29 - cmdstanpy - INFO - Chain [1] done processing
21:19:31 - cmdstanpy - INFO - Chain [1] start processing
21:19:31 - cmdstanpy - INFO - Chain [1] done processing
21:19:32 - cmdstanpy - INFO - Chain [1] start processing
21:19:32 - cmdstanpy - INFO - Chain [1] done processing
21:19:34 - cmdstanpy - INFO - Chain [1] 

21:21:28 - cmdstanpy - INFO - Chain [1] done processing
21:21:29 - cmdstanpy - INFO - Chain [1] start processing
21:21:29 - cmdstanpy - INFO - Chain [1] done processing
21:21:30 - cmdstanpy - INFO - Chain [1] start processing
21:21:31 - cmdstanpy - INFO - Chain [1] done processing
21:21:32 - cmdstanpy - INFO - Chain [1] start processing
21:21:32 - cmdstanpy - INFO - Chain [1] done processing
21:21:33 - cmdstanpy - INFO - Chain [1] start processing
21:21:33 - cmdstanpy - INFO - Chain [1] done processing
21:21:35 - cmdstanpy - INFO - Chain [1] start processing
21:21:35 - cmdstanpy - INFO - Chain [1] done processing
21:21:36 - cmdstanpy - INFO - Chain [1] start processing
21:21:36 - cmdstanpy - INFO - Chain [1] done processing
21:21:37 - cmdstanpy - INFO - Chain [1] start processing
21:21:38 - cmdstanpy - INFO - Chain [1] done processing
21:21:39 - cmdstanpy - INFO - Chain [1] start processing
21:21:39 - cmdstanpy - INFO - Chain [1] done processing
21:21:40 - cmdstanpy - INFO - Chain [1] 

In [69]:
platinum_pred =pd.DataFrame(index= platinum['ds'][-platinum_forecasting_horizon:], columns=columns)
platinum_pred['Actual'] = list(platinum['y'][platinum.shape[0]-platinum_forecasting_horizon:])
platinum_pred['ARIMA'] = arima_preds10
platinum_pred['ARIMA-GARCH'] = arch_preds10
platinum_pred['ARIMA 2'] = arima_preds2_10
platinum_pred['ARIMA-GARCH 2'] = arch_preds2_10
platinum_pred['ARIMA 3'] = arima_preds3_10
platinum_pred['ARIMA-GARCH 3'] = arch_preds3_10
platinum_pred['Simple Exponential Smoothing'] = ses_preds10
platinum_pred['Holt\'s Exponential Smoothing'] = holt_preds10
platinum_pred['Holt-Winter\'s Exponential Smoothing'] = hw_preds10
platinum_pred['Prophet'] = prophet_preds10
platinum_pred['Prophet+ARIMA'] = prophet_arima_preds10
platinum_pred.to_csv('./results/platinum_10step_forecasting.csv')

In [70]:
results.to_csv('./results/mae.csv')